# Working code,partial working

In [12]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from webdriver_manager.chrome import ChromeDriverManager
import time
import re

options = webdriver.ChromeOptions()
# options.add_argument("--headless")  # Optional: run in background
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
url = "https://www.google.co.in/maps/place/UCO+Bank/@22.5756399,88.2757906,12z/data=!4m10!1m2!2m1!1suco+bank+branches+in+west+bengal!3m6!1s0x3a0277fe2fe8ca7f:0x85ee17e67b1d70dd!8m2!3d22.56584!4d88.35213!15sCiB1Y28gYmFuayBicmFuY2hlcyBpbiB3ZXN0IGJlbmdhbCIDiAEBkgEEYmFua-ABAA!16s%2Fg%2F11l146l65r?entry=ttu"
driver.get(url)
time.sleep(5)

# Extract branch name
try:
    name = driver.find_element(By.XPATH, '//h1[contains(@class,"DUwDvf")]').text
except:
    name = "Not found"

# Extract address
try:
    address = driver.find_element(By.XPATH, '//button[contains(@aria-label, "Address")]/div').text
except:
    address = "Not found"

# Extract rating
try:
    rating = driver.find_element(By.XPATH, '//div[contains(@aria-label, " stars")]').get_attribute("aria-label")
except:
    rating = "Not found"

# Extract pincode using regex
match = re.search(r"\b\d{6}\b", address)
pincode = match.group(0) if match else "Not found"

print("Branch Name:", name)
print("Rating:", rating)
print("Address:", address)
print("Pincode:", pincode)

# === REVIEWS ===
print("\nFetching reviews...")
try:
    # First, click on the Reviews tab (not the reviews button)
    wait = WebDriverWait(driver, 10)
    
    # This clicks on the number of reviews which opens the reviews dialog
    reviews_count = wait.until(EC.element_to_be_clickable((By.XPATH, '//button[contains(@aria-label, " reviews")]')))
    driver.execute_script("arguments[0].click();", reviews_count)
    time.sleep(3)
    
    # Now make sure we're in the Reviews tab, not Overview
    # Find the Reviews tab within the dialog and click it
    reviews_tab = wait.until(EC.element_to_be_clickable((By.XPATH, '//button[@role="tab" and contains(., "Reviews")]')))
    driver.execute_script("arguments[0].click();", reviews_tab)
    time.sleep(3)
    
    # Scroll inside the review modal to load more reviews
    scrollable_div = wait.until(EC.presence_of_element_located((By.XPATH, '//div[contains(@class, "m6QErb")]')))
    
    # Scroll multiple times to load more reviews
    for _ in range(7):
        driver.execute_script("arguments[0].scrollTop = arguments[0].scrollHeight", scrollable_div)
        time.sleep(1.5)
    
    # Wait for reviews to load
    time.sleep(2)
    
    # Get all review containers
    reviews = driver.find_elements(By.XPATH, '//div[contains(@class, "jftiEf")]')
    print(f"Found {len(reviews)} reviews:\n")
    
    # Process up to 10 reviews
    for i, review in enumerate(reviews[:10]):
        try:
            # Get reviewer name - with fallback
            try:
                reviewer = review.find_element(By.CLASS_NAME, 'd4r55').text
            except NoSuchElementException:
                reviewer = "Unknown Reviewer"
            
            # Try to expand the review if it's truncated
            try:
                more_button = review.find_element(By.XPATH, './/button[@aria-label="More"]')
                driver.execute_script("arguments[0].click();", more_button)
                time.sleep(0.5)
            except NoSuchElementException:
                pass  # No "More" button, review is already fully displayed
            
            # Get review text - with fallback
            try:
                review_text = review.find_element(By.CLASS_NAME, 'wiI7pd').text
            except NoSuchElementException:
                try:
                    # Try alternative class names
                    review_text = review.find_element(By.XPATH, './/*[contains(@class, "MyEned")]').text
                except NoSuchElementException:
                    review_text = "No review text found"
            
            # Get star rating - with fallback
            try:
                review_rating = review.find_element(By.XPATH, './/span[contains(@aria-label, "stars")]').get_attribute('aria-label')
            except NoSuchElementException:
                # Try to find stars as an image or any other element
                try:
                    stars_element = review.find_element(By.XPATH, './/*[contains(@class, "kvMYJc")]')
                    stars_count = len(stars_element.find_elements(By.TAG_NAME, 'img'))
                    review_rating = f"{stars_count} stars"
                except:
                    review_rating = "Rating not found"
            
            print(f"{i+1}. {reviewer} - {review_rating}\n   \"{review_text}\"\n")
        except Exception as e:
            print(f"Error with review {i+1}: {str(e)}")
            # Try to get whatever information we can
            try:
                partial_info = f"{i+1}. "
                try:
                    partial_info += review.find_element(By.CLASS_NAME, 'd4r55').text + " - "
                except:
                    partial_info += "Unknown Reviewer - "
                
                try:
                    partial_info += "Review text: " + review.text[:100] + "..."
                except:
                    partial_info += "Unable to extract review content"
                
                print(partial_info)
            except:
                print(f"{i+1}. Could not extract any information from this review")
            
except Exception as e:
    print("Error while scraping reviews:", e)
    
finally:
    driver.quit()

Branch Name: UCO Bank
Rating: 3.7 stars
Address: 
No 2, Ground Floor, India Exchange Place, B.B.D. Bagh, Kolkata, West Bengal 700001
Pincode: 700001

Fetching reviews...
Found 7 reviews:

1. SUBRATA SAHA - 5 stars
   "One of the important branch of UCO Bank in Kolkata. Corporate matters are deal here with specialist officers. Its situated near Tea Board Office, Kolkata. Very good wings to address all the business related solutions and the same."

2. belurmath lalbaba vidyalaya bilingual school - 0 stars
   "Wrong location"

3. Mr. Vicky - 2 stars
   "Poor service"

4. Soumavo Karmakar - 5 stars
   "Dear Soumavo Karmakar,We really appreciate you choosing UCO Bank. Thanks for your positive rating. We urge you to recommend us to others and spread the joy of Banking with us. … More"

5. Milan Kundu - 4 stars
   "Dear Milan Kundu,Receiving positive feedback is always encouraging. We will be glad to serve you again. … More"

6. pandey ji pRakash - 4 stars
   "Dear pandey ji pRakash,Receivin

## Extracting url for all branches in west bengal

In [21]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException, StaleElementReferenceException
from webdriver_manager.chrome import ChromeDriverManager
import time
import json
import csv
import os

def setup_driver():
    """Set up and return the Chrome webdriver."""
    options = webdriver.ChromeOptions()
    # Uncomment the line below to run Chrome in headless mode (no GUI)
    # options.add_argument("--headless")
    options.add_argument("--window-size=1920,1080")
    return webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)

def search_for_branches(driver):
    """Search for UCO Bank branches in West Bengal on Google Maps."""
    driver.get("https://www.google.com/maps")
    time.sleep(3)
    
    # Find search box and enter query
    search_box = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.ID, "searchboxinput"))
    )
    search_box.clear()
    search_box.send_keys("UCO Bank branches in West Bengal")
    
    # Click search button
    search_button = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.ID, "searchbox-searchbutton"))
    )
    search_button.click()
    time.sleep(5)  # Wait for results to load

def get_branch_data(driver):
    """Scroll through results and extract branch URLs."""
    branches = []
    collected_urls = set()

    print("Scrolling through results to find all branches...")

    # Wait for results to load
    WebDriverWait(driver, 20).until(
        EC.presence_of_element_located((By.XPATH, '//div[@role="feed"]'))
    )
    time.sleep(2)

    scrollable_div = driver.find_element(By.XPATH, '//div[@role="feed"]')
    last_height = driver.execute_script("return arguments[0].scrollHeight", scrollable_div)

    scroll_attempts = 0
    max_scrolls = 30  # Max scroll attempts

    while scroll_attempts < max_scrolls:
        # Scroll down
        driver.execute_script("arguments[0].scrollTo(0, arguments[0].scrollHeight);", scrollable_div)
        time.sleep(3)  # Wait for content to load

        new_height = driver.execute_script("return arguments[0].scrollHeight", scrollable_div)
        if new_height == last_height:
            scroll_attempts += 1
            print(f"No new content loaded. Attempt {scroll_attempts}/{max_scrolls}")
        else:
            scroll_attempts = 0  # Reset if new content loads
            last_height = new_height

        # Extract branches
        branch_elements = driver.find_elements(By.XPATH, '//a[contains(@href, "/maps/place/")]')
        print(f"Currently visible places: {len(branch_elements)}")

        for element in branch_elements:
            try:
                name = element.get_attribute("aria-label")
                url = element.get_attribute("href")
                if name and "UCO Bank" in name and url not in collected_urls:
                    branches.append({"name": name, "url": url})
                    collected_urls.add(url)
                    print(f"Added: {name}")
            except StaleElementReferenceException:
                continue

    print(f"Scrolling complete! Total branches found: {len(branches)}")
    return branches


def save_to_json(branches, filename="uco_bank_branches.json"):
    """Save branch data to JSON file."""
    with open(filename, 'w', encoding='utf-8') as f:
        json.dump(branches, f, ensure_ascii=False, indent=4)
    print(f"Data saved to {filename}")

def save_to_csv(branches, filename="uco_bank_branches.csv"):
    """Save branch data to CSV file."""
    with open(filename, 'w', newline='', encoding='utf-8') as f:
        writer = csv.DictWriter(f, fieldnames=["name", "url"])
        writer.writeheader()
        writer.writerows(branches)
    print(f"Data saved to {filename}")

def main():
    driver = None
    try:
        print("Starting UCO Bank branch scraper...")
        driver = setup_driver()
        search_for_branches(driver)
        branches = get_branch_data(driver)
        
        # Save data in both formats
        save_to_json(branches)
        save_to_csv(branches)
        
        print(f"Successfully scraped {len(branches)} UCO Bank branches in West Bengal!")
        
    except Exception as e:
        print(f"An error occurred: {e}")
    finally:
        if driver:
            driver.quit()
            print("Browser closed.")

if __name__ == "__main__":
    main()

Starting UCO Bank branch scraper...
Scrolling through results to find all branches...
Currently visible places: 16
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Currently visible places: 20
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Currently visible places: 28
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Currently visible places: 36
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Currently visible places: 40
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
No new content loaded. Attempt 1/30
Currently visible places: 40
Currently visible places: 56
Added: UCO Bank
Added: UCO Bank
Add

### Extracting Url of UCO bank branches for all states 

In [5]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException, StaleElementReferenceException
from webdriver_manager.chrome import ChromeDriverManager
import time
import json
import csv
import os

# List of Indian states and union territories
STATES = [
    "Andhra Pradesh", "Arunachal Pradesh", "Assam", "Bihar", "Chhattisgarh", "Goa", "Gujarat", 
    "Haryana", "Himachal Pradesh", "Jharkhand", "Karnataka", "Kerala", "Madhya Pradesh", 
    "Maharashtra", "Manipur", "Meghalaya", "Mizoram", "Nagaland", "Odisha", "Punjab", 
    "Rajasthan", "Sikkim", "Tamil Nadu", "Telangana", "Tripura", "Uttar Pradesh", 
    "Uttarakhand", "West Bengal", "Andaman and Nicobar Islands", "Chandigarh", 
    "Dadra and Nagar Haveli and Daman and Diu", "Delhi", "Jammu and Kashmir", 
    "Ladakh", "Lakshadweep", "Puducherry"
]

def setup_driver():
    """Set up and return the Chrome webdriver."""
    options = webdriver.ChromeOptions()
    # Uncomment the line below to run Chrome in headless mode (no GUI)
    # options.add_argument("--headless")
    options.add_argument("--window-size=1920,1080")
    return webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)

def search_for_branches(driver, state):
    """Search for UCO Bank branches in the specified state on Google Maps."""
    driver.get("https://www.google.com/maps")
    time.sleep(3)
    
    # Find search box and enter query
    search_box = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.ID, "searchboxinput"))
    )
    search_box.clear()
    search_box.send_keys(f"UCO Bank branches in {state}")
    
    # Click search button
    search_button = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.ID, "searchbox-searchbutton"))
    )
    search_button.click()
    time.sleep(5)  # Wait for results to load

def get_branch_data(driver, state):
    """Scroll through results and extract branch URLs for the specified state."""
    branches = []
    collected_urls = set()

    print(f"Scrolling through results to find all branches in {state}...")

    try:
        # Wait for results to load
        WebDriverWait(driver, 20).until(
            EC.presence_of_element_located((By.XPATH, '//div[@role="feed"]'))
        )
        time.sleep(2)

        scrollable_div = driver.find_element(By.XPATH, '//div[@role="feed"]')
        last_height = driver.execute_script("return arguments[0].scrollHeight", scrollable_div)

        scroll_attempts = 0
        max_scrolls = 20  # Max scroll attempts

        while scroll_attempts < max_scrolls:
            # Scroll down
            driver.execute_script("arguments[0].scrollTo(0, arguments[0].scrollHeight);", scrollable_div)
            time.sleep(3)  # Wait for content to load

            new_height = driver.execute_script("return arguments[0].scrollHeight", scrollable_div)
            if new_height == last_height:
                scroll_attempts += 1
                print(f"No new content loaded. Attempt {scroll_attempts}/{max_scrolls}")
            else:
                scroll_attempts = 0  # Reset if new content loads
                last_height = new_height

            # Extract branches
            branch_elements = driver.find_elements(By.XPATH, '//a[contains(@href, "/maps/place/")]')
            print(f"Currently visible places in {state}: {len(branch_elements)}")

            for element in branch_elements:
                try:
                    name = element.get_attribute("aria-label")
                    url = element.get_attribute("href")
                    if name and "UCO Bank" in name and url not in collected_urls:
                        branches.append({"name": name, "url": url, "state": state})
                        collected_urls.add(url)
                        print(f"Added: {name}")
                except StaleElementReferenceException:
                    continue

    except Exception as e:
        print(f"Error while scraping {state}: {e}")
    
    print(f"Scrolling complete for {state}! Total branches found: {len(branches)}")
    return branches

def create_output_directories():
    """Create output directories for JSON and CSV files."""
    os.makedirs("uco_bank_data", exist_ok=True)
    os.makedirs("uco_bank_data/json", exist_ok=True)
    os.makedirs("uco_bank_data/csv", exist_ok=True)

def save_to_json(branches, state):
    """Save branch data to JSON file."""
    filename = f"uco_bank_data/json/uco_bank_{state.lower().replace(' ', '_')}.json"
    with open(filename, 'w', encoding='utf-8') as f:
        json.dump(branches, f, ensure_ascii=False, indent=4)
    print(f"Data saved to {filename}")

def save_to_csv(branches, state):
    """Save branch data to CSV file."""
    filename = f"uco_bank_data/csv/uco_bank_{state.lower().replace(' ', '_')}.csv"
    with open(filename, 'w', newline='', encoding='utf-8') as f:
        writer = csv.DictWriter(f, fieldnames=["name", "url", "state"])
        writer.writeheader()
        writer.writerows(branches)
    print(f"Data saved to {filename}")

def save_all_states_summary(all_branches):
    """Save a summary JSON file containing all states and branch counts."""
    state_summary = {}
    for state, branches in all_branches.items():
        state_summary[state] = {
            "branch_count": len(branches),
            "json_file": f"uco_bank_data/json/uco_bank_{state.lower().replace(' ', '_')}.json",
            "csv_file": f"uco_bank_data/csv/uco_bank_{state.lower().replace(' ', '_')}.csv"
        }
    
    with open("uco_bank_data/state_summary.json", 'w', encoding='utf-8') as f:
        json.dump(state_summary, f, ensure_ascii=False, indent=4)
    print(f"Summary saved to uco_bank_data/state_summary.json")

def main():
    driver = None
    all_branches = {}
    
    try:
        print("Starting UCO Bank branch scraper for all Indian states...")
        create_output_directories()
        driver = setup_driver()
        
        for state in STATES:
            print(f"\n{'='*50}")
            print(f"Processing state: {state}")
            print(f"{'='*50}")
            
            search_for_branches(driver, state)
            branches = get_branch_data(driver, state)
            
            # Save data for this state in both formats
            save_to_json(branches, state)
            save_to_csv(branches, state)
            
            # Store in our all_branches dictionary
            all_branches[state] = branches
            
            print(f"Successfully scraped {len(branches)} UCO Bank branches in {state}!")
            time.sleep(2)  # Brief pause between states
        
        # Save a summary file with all states
        save_all_states_summary(all_branches)
        
        print("\nAll states processed successfully!")
        
    except Exception as e:
        print(f"An error occurred in main execution: {e}")
    finally:
        if driver:
            driver.quit()
            print("Browser closed.")

if __name__ == "__main__":
    main()

Starting UCO Bank branch scraper for all Indian states...

Processing state: Andhra Pradesh
Scrolling through results to find all branches in Andhra Pradesh...
Currently visible places in Andhra Pradesh: 16
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Currently visible places in Andhra Pradesh: 20
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank - Hanuman Junction Branch
Currently visible places in Andhra Pradesh: 28
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank
Added: UCO Bank - Anantavaram Branch
Added: UCO Bank
Added: UCO Bank
Currently visible places in Andhra Pradesh: 30
Added: UCO Bank
Added: UCO Bank
No new content loaded. Attempt 1/20
Currently visible places in Andhra Pradesh: 30
No new content loaded. Attempt 2/20
Currently visible plac

## 2nd best code(Production ready for extracting review of  all branches from one State)

In [3]:
import json
import os
import pandas as pd
import time
import re
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException, ElementClickInterceptedException, StaleElementReferenceException
from webdriver_manager.chrome import ChromeDriverManager

# Path to your JSON file containing branch URLs
JSON_PATH = r"C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping\uco_bank_branches.json"

def load_branch_urls(json_path, limit=5):
    """
    Load branch URLs from a JSON file.
    It handles various possible JSON formats.
    Only the first 'limit' entries are returned.
    """
    try:
        with open(json_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except UnicodeDecodeError:
        # Try with a different encoding if UTF-8 fails
        with open(json_path, 'r', encoding='latin-1') as f:
            data = json.load(f)
    except Exception as e:
        print("Error reading JSON file:", e)
        return []
    
    urls = []
    count = 0
    
    # Print first item for debugging
    if data and len(data) > 0:
        print("First item in JSON data:", data[0])
    
    # Handle different JSON formats
    if isinstance(data, list):
        for item in data:
            if count >= limit:
                break
                
            if isinstance(item, dict):
                # Handle dictionary format
                if "url" in item:
                    urls.append(item["url"])
                    count += 1
                elif isinstance(item, dict) and all(isinstance(v, str) for v in item.values()):
                    # Dictionary with string values but no 'url' key
                    # Try to find a value that looks like a URL
                    for value in item.values():
                        if value.startswith("http"):
                            urls.append(value)
                            count += 1
                            break
            elif isinstance(item, str):
                # Handle string format
                if item.startswith("http"):
                    urls.append(item)
                    count += 1
    else:
        print("Unexpected JSON format. Expected a list.")
    
    return urls
    
##
def scroll_to_load_all_reviews(driver, max_scrolls=30):
    """
    Scroll the reviews container to load more reviews dynamically.
    Returns the number of reviews loaded.
    """
    print("Starting to scroll to load more reviews...")
    
    # Wait for reviews to be initially loaded
    time.sleep(3)
    
    # Try different scrollable container selectors
    scrollable_div_xpaths = [
        '//div[contains(@class, "m6QErb")]//div[@role="feed"]',
        '//div[contains(@class, "DxyBCb")]',
        '//div[@role="feed"]',
        '//div[contains(@class, "section-scrollbox")]',
        '//div[contains(@class, "m6QErb-HiaYvf")]',
        '//div[contains(@class, "m6QErb")]/div',
        '//div[contains(@class, "review-dialog-list")]',
        # Add more precise selectors for Google Maps reviews
        '//div[@data-review-id]/ancestor::div[@role="feed"]',
        '//div[contains(@class, "siAUzd-neVct")]',
        '//div[@role="main"]',
        '//div[contains(@class, "section-layout")]'
    ]
    
    # Find the scrollable container
    scrollable = None
    for xpath in scrollable_div_xpaths:
        try:
            elements = driver.find_elements(By.XPATH, xpath)
            if elements:
                for element in elements:
                    try:
                        # Check if element is scrollable by examining its properties
                        scroll_height = driver.execute_script("return arguments[0].scrollHeight", element)
                        client_height = driver.execute_script("return arguments[0].clientHeight", element)
                        
                        if scroll_height > client_height:
                            scrollable = element
                            print(f"Found scrollable container with xpath: {xpath}")
                            print(f"Scroll height: {scroll_height}, Client height: {client_height}")
                            break
                    except Exception as e:
                        print(f"Error checking element scrollability: {e}")
                        continue
            if scrollable:
                break
        except Exception:
            continue
    
    if not scrollable:
        print("Could not find scrollable container. Trying direct document scrolling.")
        scrollable = driver.find_element(By.TAG_NAME, 'body')
    
    # Count reviews before scrolling
    review_elements = count_review_elements(driver)
    print(f"Initial review count: {review_elements}")
    
    # Track the last review count to detect when no new reviews are loaded
    last_review_count = 0
    unchanged_count = 0
    scroll_count = 0
    
    # Scroll until we hit maximum or no new reviews load after multiple attempts
    while scroll_count < max_scrolls and unchanged_count < 5:
        try:
            # Try multiple scroll methods
            
            # Method 1: Standard JavaScript scroll
            driver.execute_script("arguments[0].scrollTop = arguments[0].scrollHeight", scrollable)
            print(f"Method 1: Scrolled container, attempt {scroll_count+1}")
            
            # Method 2: Alternative scroll approach
            driver.execute_script("""
                var element = arguments[0];
                element.scrollTo({
                    top: element.scrollHeight,
                    behavior: 'smooth'
                });
            """, scrollable)
            print(f"Method 2: Smooth scrolled container")
            
            # Method 3: Scroll by a specific amount
            driver.execute_script("arguments[0].scrollTop += 1000;", scrollable)
            print(f"Method 3: Incremental scroll by 1000px")
            
            # Method 4: Try to click on the last visible review to ensure focus
            try:
                reviews = driver.find_elements(By.XPATH, '//div[@data-review-id]')
                if reviews:
                    last_review = reviews[-1]
                    driver.execute_script("arguments[0].scrollIntoView({behavior: 'smooth', block: 'end'});", last_review)
                    print(f"Method 4: Scrolled last review into view")
            except Exception as e:
                print(f"Method 4 failed: {e}")
            
            # Method 5: Direct body scroll (a fallback)
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
            print(f"Method 5: Direct body scroll")
            
            # Wait longer for new content to load
            time.sleep(3)
            
            # Count reviews after scrolling
            current_reviews = count_review_elements(driver)
            print(f"Current review count: {current_reviews}")
            
            if current_reviews == last_review_count:
                unchanged_count += 1
                print(f"No new reviews loaded. Unchanged count: {unchanged_count}")
                
                # Take screenshot for debugging if no new reviews loaded
                if unchanged_count == 1:
                    try:
                        screenshot_path = f"scroll_debug_{scroll_count}.png"
                        driver.save_screenshot(screenshot_path)
                        print(f"Saved debug screenshot to {screenshot_path}")
                    except Exception:
                        pass
                        
                # Try to click "Show More Reviews" button if no progress
                try_click_more_reviews(driver)
            else:
                unchanged_count = 0
                print(f"Success! Loaded {current_reviews - last_review_count} new reviews")
            
            last_review_count = current_reviews
            scroll_count += 1
            
        except Exception as e:
            print(f"Error while scrolling: {e}")
            break
    
    final_review_count = count_review_elements(driver)
    print(f"Finished scrolling. Total reviews loaded: {final_review_count}")
    return final_review_count
    
##       

def try_click_more_reviews(driver):
    """Attempt to click on "More Reviews" or similar buttons."""
    more_reviews_button_xpaths = [
        '//button[contains(text(), "More reviews")]',
        '//button[contains(text(), "Show more")]',
        '//button[contains(@aria-label, "more reviews")]',
        '//button[contains(@aria-label, "Show more reviews")]',
        '//span[contains(text(), "more reviews")]/ancestor::button',
        '//div[contains(text(), "More reviews") and @role="button"]',
        # Add more Google Maps specific selectors
        '//button[contains(@data-tab-index, "0") and contains(text(), "review")]',
        '//button[contains(@class, "HHrUdb")]',  # Common class for buttons in Google Maps
        '//span[text()="More"]/ancestor::button',
        '//div[contains(@jsaction, "pane.review.expandReview")]',
        '//div[text()="Show more reviews"]/ancestor::*[@role="button"]'
    ]
    
    for xpath in more_reviews_button_xpaths:
        try:
            more_buttons = driver.find_elements(By.XPATH, xpath)
            for more_button in more_buttons:
                if more_button.is_displayed():
                    print(f"Found 'More Reviews' button with text: {more_button.text}")
                    try:
                        # Try the regular click first
                        more_button.click()
                        print("Clicked 'More Reviews' button with direct click")
                    except Exception as e:
                        print(f"Direct click failed: {e}, trying JavaScript click")
                        try:
                            # Try JavaScript click as fallback
                            driver.execute_script("arguments[0].click();", more_button)
                            print("Clicked 'More Reviews' button with JavaScript")
                        except Exception as e:
                            print(f"JavaScript click also failed: {e}")
                            continue
                    time.sleep(3)  # Wait longer for new reviews to load
                    return True
        except Exception as e:
            print(f"Error with xpath {xpath}: {e}")
            continue
    
    # Additional fallback method: Look for "more reviews" text and click nearby
    try:
        more_text_elements = driver.find_elements(By.XPATH, '//*[contains(text(), "more review") or contains(text(), "More review")]')
        for el in more_text_elements:
            if el.is_displayed():
                print(f"Found text mentioning more reviews: {el.text}")
                # Click on the element or its parent
                try:
                    el.click()
                    print("Clicked directly on text element")
                except Exception:
                    try:
                        parent = driver.execute_script("return arguments[0].parentNode;", el)
                        driver.execute_script("arguments[0].click();", parent)
                        print("Clicked on parent of text element")
                    except Exception:
                        continue
                time.sleep(3)
                return True
    except Exception as e:
        print(f"Error in fallback method: {e}")
    
    return False

def count_review_elements(driver):
    """Count the number of review elements currently on the page."""
    review_container_xpaths = [
        '//div[contains(@class, "jftiEf")]',
        '//div[contains(@class, "gws-localreviews__google-review")]',
        '//div[contains(@data-review-id, "Ch")]',
        '//div[@data-review-id]',
        '//div[@jsaction="mouseover:pane.review.in"]',
        '//div[starts-with(@class, "m") and contains(@class, "xn")]',
        '//div[contains(@class, "fontBodyMedium")]//div[contains(@class, "MyEned")]',
        '//div[@jscontroller and contains(@class, "fontBodyMedium")]',
        '//*[@class="m6QErb DxyBCb kA9KIf dS8AEf"]//div[@data-review-id and @aria-label]',
        # Add more specific selectors for Google Maps reviews
        '//div[contains(@class, "jJc9Ad")]',
        '//div[contains(@class, "siAUzd-neVct") and @data-review-id]',
        '//div[contains(@aria-label, "reviews") or contains(@aria-label, "review")]'
    ]
    
    max_count = 0
    for xpath in review_container_xpaths:
        try:
            reviews = driver.find_elements(By.XPATH, xpath)
            current_count = len(reviews)
            if current_count > max_count:
                max_count = current_count
                print(f"Found {current_count} reviews with xpath: {xpath}")
        except Exception:
            continue
    
    # If we still can't find reviews, try a more general approach
    if max_count == 0:
        try:
            # Look for elements that might contain reviewer names
            reviewer_elements = driver.find_elements(By.XPATH, '//div[contains(@class, "d4r55") or contains(@class, "DHIhE")]')
            if reviewer_elements:
                max_count = len(reviewer_elements)
                print(f"Found {max_count} possible reviews based on reviewer elements")
        except Exception:
            pass
    
    return max_count
def navigate_to_reviews_tab(driver, url, branch_name=""):
    """
    Navigate to the reviews tab using various methods.
    Returns True if successfully navigated to reviews.
    """
    print(f"\nAttempting to navigate to reviews tab for: {branch_name}")
    
    # First try: Direct navigation via URL modification
    try:
        # Extract place ID from the URL
        match = re.search(r"!1s([^!]+)!", url)
        if match:
            place_id = match.group(1)
            print(f"Extracted place ID: {place_id}")
            
            # Construct a direct URL to the reviews tab
            safe_branch_name = branch_name.replace(' ', '+') if branch_name else "location"
            reviews_url = f"https://www.google.com/maps/place/{safe_branch_name}/@0,0,10z/data=!4m7!3m6!1s{place_id}!8m2!3d0!4d0!9m1!1b1"
            print(f"Navigating directly to reviews URL: {reviews_url}")
            
            driver.get(reviews_url)
            time.sleep(5)  # Wait for the page to load
            
            # Check if we're on a page with reviews
            if count_review_elements(driver) > 0:
                print("Successfully navigated to reviews via URL modification")
                return True
            else:
                print("No reviews found via URL modification, trying alternative methods")
        else:
            print("Could not extract place ID from URL")
    except Exception as e:
        print(f"Error during direct navigation to reviews: {e}")
    
    # Second try: Click on the reviews tab or button
    try:
        # Try various ways to access the reviews section
        wait = WebDriverWait(driver, 15)
        
        # First make sure we're on the main page if URL modification failed
        if not url.endswith("/reviews"):
            driver.get(url)
            time.sleep(5)
        
        # Look for reviews button with various xpaths
        review_button_xpaths = [
            '//button[contains(@aria-label, " reviews")]',
            '//button[contains(@aria-label, "reviews")]',
            '//div[contains(@role, "button")][contains(., "reviews")]',
            '//div[contains(@jsaction, "pane.rating.moreReviews")]',
            '//span[contains(text(), "reviews")]/ancestor::button',
            '//div[contains(@class, "F7nice")]/span[2]/span/span',
            '//button[contains(@jsaction, "pane.rating.moreReviews")]',
            '//button[contains(@data-tab-index, "0") and contains(., "review")]',
            # New patterns specifically for reviews tab
            '//button[@data-tab="reviews" or @data-item-id="reviews"]',
            '//button[contains(@aria-label, "Reviews")]',
            '//div[contains(@role, "tab") and contains(., "review")]'
        ]
        
        for xpath in review_button_xpaths:
            try:
                print(f"Trying to find reviews button with: {xpath}")
                reviews_button = wait.until(EC.element_to_be_clickable((By.XPATH, xpath)))
                print(f"Found reviews button with xpath: {xpath}")
                print(f"Button text: {reviews_button.text}")
                
                # Try to click the button
                try:
                    reviews_button.click()
                    print("Clicked reviews button with direct click")
                except Exception:
                    driver.execute_script("arguments[0].click();", reviews_button)
                    print("Clicked reviews button with JavaScript")
                
                time.sleep(4)
                
                # Check if reviews are visible
                if count_review_elements(driver) > 0:
                    print("Successfully navigated to reviews via button click")
                    return True
                else:
                    print("Clicked button but no reviews found, trying next method")
            except Exception as e:
                print(f"Error with xpath {xpath}: {e}")
                continue
    except Exception as e:
        print(f"Error navigating to reviews tab: {e}")
    
    # Third try: Look for a reviews section that's already visible
    if count_review_elements(driver) > 0:
        print("Reviews already visible on page")
        return True
    
    print("All navigation methods to reviews tab failed")
    return False

# Improved version of the extract_branch_data function with better review identification
def extract_branch_data(driver, url):
    """Extract branch details and reviews from a direct Google Maps branch URL."""
    print(f"\nLoading URL: {url}")
    try:
        driver.get(url)
        time.sleep(5)  # Adjust if the page loads slowly
    except Exception as e:
        print(f"Error loading URL: {e}")
        return {
            "name": "Error Loading Page",
            "address": "N/A",
            "rating": "N/A",
            "pincode": "N/A",
            "reviews": [],
            "url": url
        }

    # --- Extract Basic Branch Details ---
    branch_name = "Not found"
    address = "Not found"
    rating = "Not found"
    pincode = "Not found"
    
    try:
        branch_name = driver.find_element(By.XPATH, '//h1[contains(@class,"DUwDvf")]').text
        print(f"Found branch name: {branch_name}")
    except Exception as e:
        print(f"Error finding branch name: {e}")
    
    try:
        address = driver.find_element(By.XPATH, '//button[contains(@aria-label, "Address")]/div').text
        print(f"Found address: {address}")
    except Exception as e:
        try:
            # Alternative way to find address
            address_elements = driver.find_elements(By.XPATH, '//div[contains(@class, "Io6YTe")]/div')
            if address_elements:
                address = address_elements[0].text
                print(f"Found address (alternative): {address}")
        except Exception:
            print("Error finding address using both methods")
    
    try:
        rating = driver.find_element(By.XPATH, '//div[contains(@aria-label, " stars")]').get_attribute("aria-label")
        print(f"Found rating: {rating}")
    except Exception as e:
        print(f"Error finding rating: {e}")
        
    if address != "Not found":
        match = re.search(r"\b\d{6}\b", address)
        pincode = match.group(0) if match else "Not found"
    
    print("Branch Name:", branch_name)
    print("Rating:", rating)
    print("Address:", address)
    print("Pincode:", pincode)
    
    # --- Extract Reviews ---
    reviews_list = []
    print("\nFetching reviews for:", branch_name)
    
    # Save a screenshot to debug review issues
    try:
        screenshot_path = os.path.join(os.path.dirname(JSON_PATH), f"{branch_name}_screenshot.png".replace(" ", "_"))
        driver.save_screenshot(screenshot_path)
        print(f"Saved screenshot to {screenshot_path}")
    except Exception as e:
        print(f"Could not save screenshot: {e}")
    
    # Navigate to the reviews tab
    if navigate_to_reviews_tab(driver, url, branch_name):
        # Successfully navigated to reviews tab
        # Now scroll to load all available reviews
        print("Successfully navigated to reviews tab, now loading all reviews...")
        
        # Scroll to load all reviews
        total_reviews = scroll_to_load_all_reviews(driver, max_scrolls=30)
        print(f"Loaded a total of {total_reviews} reviews")
        
        # Process the reviews
        try:
            # Find parent review containers - these will contain both customer reviews and potentially owner responses
            primary_review_xpaths = [
                '//div[contains(@class, "jftiEf")]',
                '//div[contains(@data-review-id, "Ch")]',
                '//div[@data-review-id]',
                '//div[contains(@class, "fontBodyMedium")]//div[contains(@class, "MyEned")]/ancestor::div[@data-review-id]',
                '//*[@class="m6QErb DxyBCb kA9KIf dS8AEf"]//div[@data-review-id and @aria-label]'
            ]
            
            primary_reviews = []
            for xpath in primary_review_xpaths:
                try:
                    review_elements = driver.find_elements(By.XPATH, xpath)
                    if review_elements and len(review_elements) > 0:
                        primary_reviews = review_elements
                        print(f"Found {len(primary_reviews)} primary review containers with xpath: {xpath}")
                        break
                except Exception as e:
                    print(f"Error with primary review xpath {xpath}: {e}")
            
            # Set max reviews to process (can be adjusted based on need)
            max_reviews_to_process = len(primary_reviews)
            print(f"Processing {max_reviews_to_process} primary review containers...\n")
            
            processed_reviews = 0
            for i, review_container in enumerate(primary_reviews[:max_reviews_to_process]):
                try:
                    # Save individual review HTML for debugging (first few only)
                    if i < 3:
                        try:
                            review_html = review_container.get_attribute('outerHTML')
                            review_debug_path = os.path.join(os.path.dirname(JSON_PATH), f"{branch_name}_review_{i+1}_debug.txt".replace(" ", "_"))
                            with open(review_debug_path, 'w', encoding='utf-8') as f:
                                f.write(review_html)
                            print(f"Saved review {i+1} HTML to {review_debug_path}")
                        except Exception:
                            pass
                    
                    # IMPORTANT: First check if this entire container is an owner response
                    is_full_container_owner_response = False
                    try:
                        # Look for indicators that the entire container is an owner response
                        owner_container_indicators = [
                            './/div[contains(text(), "Response from the owner")]',
                            './/div[contains(@class, "CDe7pd")][contains(text(), "owner")]',
                            './/div[contains(text(), "Owner response")]',
                            './/div[contains(@class, "JsEyr")][contains(text(), "owner")]',
                            './/div[@jslog and contains(text(), "owner")]'
                        ]
                        
                        for xpath in owner_container_indicators:
                            owner_indicators = review_container.find_elements(By.XPATH, xpath)
                            if owner_indicators and len(owner_indicators) > 0:
                                print(f"Container {i+1} is an owner response - skipping")
                                is_full_container_owner_response = True
                                break
                    except Exception as e:
                        print(f"Error checking if container {i+1} is owner response: {e}")
                    
                    if is_full_container_owner_response:
                        continue
                    
                    # Process customer review within this container
                    # First, identify the reviewer information
                    reviewer = "Unknown Reviewer"
                    reviewer_xpaths = [
                        './/div[contains(@class, "d4r55")]',
                        './/div[@class="TSUbDb"]',
                        './/div[contains(@class, "WNxzHc")]',
                        './/div[contains(@class, "tPuDnb")]',
                        './/span[@class="x3AX1-LfntMc-header-title-title"]/span',
                        './/div[@class="DHIhE"]',
                        './/div[@role="text" and @class]',
                        './/a[contains(@href, "contrib")]',
                        './/div[contains(@class, "WNxzHc")]//span'
                    ]
                    
                    for xpath in reviewer_xpaths:
                        try:
                            reviewer_elements = review_container.find_elements(By.XPATH, xpath)
                            if reviewer_elements and reviewer_elements[0].text and len(reviewer_elements[0].text) > 0:
                                reviewer = reviewer_elements[0].text
                                break
                        except Exception:
                            continue
                    
                    # Skip if reviewer name indicates this is the owner
                    if (reviewer.lower() == "owner" or 
                        "owner" in reviewer.lower() or 
                        (branch_name != "Not found" and branch_name.lower() in reviewer.lower())):
                        print(f"Skipping review {i+1} as reviewer '{reviewer}' appears to be the owner")
                        continue
                    
                    # Expand the review if it's truncated
                    try:
                        more_button_xpaths = [
                            './/button[@aria-label="More"]',
                            './/button[contains(text(), "More")]',
                            './/button[contains(@class, "w8nwRe")]',
                            './/button[text()="More"]',
                            './/button[contains(@jsaction, "pane.review.expandReview")]'
                        ]
                        
                        for xpath in more_button_xpaths:
                            more_buttons = review_container.find_elements(By.XPATH, xpath)
                            for more_button in more_buttons:
                                if more_button.is_displayed():
                                    try:
                                        more_button.click()
                                    except Exception:
                                        driver.execute_script("arguments[0].click();", more_button)
                                    print(f"Expanded review {i+1}")
                                    time.sleep(0.5)
                                    break
                    except Exception as e:
                        print(f"Error expanding review {i+1}: {e}")
                    
                    # Get review text - focus on the main customer review, not the owner response
                    review_text = "No review text found"
                    text_xpaths = [
                        './/span[contains(@class, "wiI7pd")]',
                        './/div[contains(@class, "wiI7pd")]',
                        './/*[contains(@class, "MyEned")]',
                        './/*[contains(@class, "review-full-text")]',
                        './/span[contains(@class, "review-full-text")]',
                        './/div[@class="MyEned"]',
                        './/div[@data-js-log-root]',
                        './/div[contains(@class, "RBcccd")]/div[not(contains(@class, "CDe7pd"))]/span',
                        './/div[contains(@class, "RBcccd")]/div[not(contains(@class, "CDe7pd"))]/div'
                    ]
                    
                    # First try to find actual review text containers that are not owner responses
                    for xpath in text_xpaths:
                        try:
                            # Get all potential text elements
                            text_elements = review_container.find_elements(By.XPATH, xpath)
                            
                            # Filter out elements that are inside owner response sections
                            filtered_elements = []
                            for element in text_elements:
                                # Check if this element is inside an owner response section
                                parent_is_owner = False
                                try:
                                    # Check if any parent element has owner response indicators
                                    owner_indicators = element.find_elements(By.XPATH, 'ancestor::div[contains(text(), "Response from the owner") or contains(@class, "CDe7pd") or contains(text(), "Owner response")]')
                                    if owner_indicators and len(owner_indicators) > 0:
                                        parent_is_owner = True
                                except Exception:
                                    pass
                                
                                if not parent_is_owner and element.text and len(element.text) > 0:
                                    filtered_elements.append(element)
                            
                            # Use the first valid text element
                            if filtered_elements:
                                review_text = filtered_elements[0].text
                                break
                        except Exception:
                            continue
                    
                    # Get review rating
                    review_rating = "Rating not found"
                    rating_xpaths = [
                        './/span[contains(@aria-label, "stars")]',
                        './/*[contains(@class, "kvMYJc")]',
                        './/*[contains(@aria-label, "Rated")]',
                        './/div[@role="img" and contains(@aria-label, "stars")]',
                        './/g-review-stars',
                        './/*[contains(@class, "IQDGvf")]',
                        './/span[@role="img"]'
                    ]
                    
                    for xpath in rating_xpaths:
                        try:
                            rating_elements = review_container.find_elements(By.XPATH, xpath)
                            if rating_elements:
                                aria_label = rating_elements[0].get_attribute('aria-label')
                                if aria_label and "star" in aria_label.lower():
                                    review_rating = aria_label
                                    break
                                
                                # If no aria-label, try to count star images
                                star_elements = rating_elements[0].find_elements(By.TAG_NAME, 'img')
                                if star_elements:
                                    review_rating = f"{len(star_elements)} stars"
                                    break
                        except Exception:
                            continue
                    
                    # If all direct methods fail, try to find any text with "stars" or "rated"
                    if review_rating == "Rating not found":
                        try:
                            rating_texts = review_container.find_elements(By.XPATH, './/*[contains(text(), "star") or contains(text(), "rated")]')
                            for el in rating_texts:
                                if "star" in el.text.lower() or "rated" in el.text.lower():
                                    review_rating = el.text
                                    break
                        except Exception:
                            pass
                    
                    # Special check for star-only reviews
                    is_star_only_review = (review_text == "No review text found" or not review_text.strip())
                    has_valid_rating = (review_rating != "Rating not found" and "star" in review_rating.lower())
                    
                    # Only add valid reviews that are not owner responses
                    if not is_star_only_review or (is_star_only_review and has_valid_rating):
                        reviews_list.append({
                            "reviewer": reviewer,
                            "rating": review_rating,
                            "text": review_text
                        })
                        processed_reviews += 1
                        print(f"{i+1}. {reviewer} - {review_rating}\n   \"{review_text[:100]}{'...' if len(review_text) > 100 else ''}\"\n")
                    else:
                        print(f"Skipping review {i+1} as it lacks both text and a valid rating")
                    
                except StaleElementReferenceException:
                    print(f"Stale element for review {i+1}, attempting to refresh elements")
                    # Refresh all reviews
                    for xpath in primary_review_xpaths:
                        try:
                            primary_reviews = driver.find_elements(By.XPATH, xpath)
                            if primary_reviews and len(primary_reviews) > i:
                                break
                        except Exception:
                            continue
                except Exception as e:
                    print(f"Error processing review {i+1}: {str(e)}")
            
            print(f"Successfully processed {processed_reviews} reviews out of {len(primary_reviews)} found")
            
        except Exception as e:
            print(f"Error processing reviews: {e}")
    else:
        print("Could not navigate to reviews tab")
    
    # Return all gathered details for this branch
    return {
        "name": branch_name,
        "address": address,
        "rating": rating,
        "pincode": pincode,
        "reviews": reviews_list,
        "url": url
    }
def main():
    # Load branch URLs from JSON file (limiting to 5 for testing)
    # Change the limit parameter when ready for full production run
    branch_urls = load_branch_urls(JSON_PATH, limit=5)
    if not branch_urls:
        print("No URLs loaded from JSON. Exiting.")
        return
    
    print(f"Loaded {len(branch_urls)} URLs for processing")
    
    # Set up the Chrome driver with anti-detection measures
    options = webdriver.ChromeOptions()
    # Adding user agent to avoid detection
    options.add_argument("user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36")
    # Add additional options to make scraping more robust
    options.add_argument("--disable-blink-features=AutomationControlled")
    options.add_experimental_option("excludeSwitches", ["enable-automation"])
    options.add_experimental_option("useAutomationExtension", False)
    
    # Uncomment below to run headless if desired:
    # options.add_argument("--headless")
    # options.add_argument("--window-size=1920,1080")
    
    driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
    
    # Execute CDP commands to prevent detection
    driver.execute_cdp_cmd("Page.addScriptToEvaluateOnNewDocument", {
        "source": """
        Object.defineProperty(navigator, 'webdriver', {
            get: () => undefined
        })
        """
    })
    
    # Set a longer page load timeout
    driver.set_page_load_timeout(30)
    
    all_branch_data = []
    # Process each branch URL individually
    try:
        for i, url in enumerate(branch_urls, 1):
            print(f"\n--- Processing branch {i}/{len(branch_urls)} ---")
            branch_data = extract_branch_data(driver, url)
            all_branch_data.append(branch_data)
            print(f"Completed branch {i} with {len(branch_data['reviews'])} reviews")
            time.sleep(5)  # Brief pause between branches
    except Exception as e:
        print(f"Error in main processing loop: {e}")
    finally:
        driver.quit()
        print("Driver closed successfully")
    
    # Create DataFrames for branch details and reviews
    try:
        if all_branch_data:
            branches_df = pd.DataFrame([{
                "Branch Name": b["name"],
                "Address": b["address"],
                "Rating": b["rating"],
                "Pincode": b["pincode"],
                "URL": b["url"]
            } for b in all_branch_data])
            
            reviews_data = []
            for b in all_branch_data:
                for rev in b["reviews"]:
                    reviews_data.append({
                        "Branch Name": b["name"],
                        "Reviewer": rev["reviewer"],
                        "Review Rating": rev["rating"],
                        "Review Text": rev["text"]
                    })
            
            reviews_df = pd.DataFrame(reviews_data)
            
            # Save the results
            output_dir = os.path.dirname(JSON_PATH)
            branches_df.to_csv(os.path.join(output_dir, "uco_branches_details.csv"), index=False, encoding='utf-8')
            reviews_df.to_csv(os.path.join(output_dir, "uco_branches_reviews.csv"), index=False, encoding='utf-8')
            
            # Save as JSON
            with open(os.path.join(output_dir, "uco_branches_details.json"), 'w', encoding='utf-8') as f:
                json.dump(all_branch_data, f, indent=4, ensure_ascii=False)
                
            print(f"\nFiles saved to {output_dir}")
            
            print("\nSummary of results:")
            for branch in all_branch_data:
                print(f"Branch: {branch['name']}, Reviews: {len(branch['reviews'])}")
        else:
            print("No branch data was collected.")
    except Exception as e:
        print(f"Error while creating output: {e}")

if __name__ == "__main__":
    main()

Error reading JSON file: [Errno 2] No such file or directory: 'C:\\Users\\rzzzc\\BFARPy\\Python\\4th Sem\\UCO_google_review_scrapping\\uco_bank_branches.json'
No URLs loaded from JSON. Exiting.


## Best Code to load URL of all branches from all States to extract reviews

In [ ]:
import json
import os
import pandas as pd
import time
import re
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException, ElementClickInterceptedException, StaleElementReferenceException
from webdriver_manager.chrome import ChromeDriverManager
import glob

# Base directory for JSON files
BASE_DIR = r"C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping"
# Path to the JSON folder containing all state JSON files
JSON_FOLDER = os.path.join(BASE_DIR, "uco_bank_data", "json")

def load_branch_urls_from_file(json_path, limit=None):
    """
    Load branch URLs from a single JSON file.
    It handles various possible JSON formats.
    Only the first 'limit' entries are returned if specified.
    """
    try:
        with open(json_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except UnicodeDecodeError:
        # Try with a different encoding if UTF-8 fails
        with open(json_path, 'r', encoding='latin-1') as f:
            data = json.load(f)
    except Exception as e:
        print(f"Error reading JSON file {json_path}: {e}")
        return []
    
    urls = []
    count = 0
    
    # Print first item for debugging
    if data and len(data) > 0:
        print(f"First item in JSON data ({os.path.basename(json_path)}):", data[0])
    
    # Handle different JSON formats
    if isinstance(data, list):
        for item in data:
            if limit is not None and count >= limit:
                break
                
            if isinstance(item, dict):
                # Handle dictionary format
                if "url" in item:
                    urls.append(item["url"])
                    count += 1
                elif isinstance(item, dict) and all(isinstance(v, str) for v in item.values()):
                    # Dictionary with string values but no 'url' key
                    # Try to find a value that looks like a URL
                    for value in item.values():
                        if value.startswith("http"):
                            urls.append(value)
                            count += 1
                            break
            elif isinstance(item, str):
                # Handle string format
                if item.startswith("http"):
                    urls.append(item)
                    count += 1
    else:
        print(f"Unexpected JSON format in {json_path}. Expected a list.")
    
    print(f"Loaded {len(urls)} URLs from {os.path.basename(json_path)}")
    return urls

def get_all_json_files():
    """Get all JSON files from the JSON folder"""
    json_pattern = os.path.join(JSON_FOLDER, "*.json")
    json_files = glob.glob(json_pattern)
    print(f"Found {len(json_files)} JSON files in {JSON_FOLDER}")
    return json_files

def scroll_to_load_all_reviews(driver, max_scrolls=30):
    """
    Scroll the reviews container to load more reviews dynamically.
    Returns the number of reviews loaded.
    """
    print("Starting to scroll to load more reviews...")
    
    # Wait for reviews to be initially loaded
    time.sleep(3)
    
    # Try different scrollable container selectors
    scrollable_div_xpaths = [
        '//div[contains(@class, "m6QErb")]//div[@role="feed"]',
        '//div[contains(@class, "DxyBCb")]',
        '//div[@role="feed"]',
        '//div[contains(@class, "section-scrollbox")]',
        '//div[contains(@class, "m6QErb-HiaYvf")]',
        '//div[contains(@class, "m6QErb")]/div',
        '//div[contains(@class, "review-dialog-list")]',
        # Add more precise selectors for Google Maps reviews
        '//div[@data-review-id]/ancestor::div[@role="feed"]',
        '//div[contains(@class, "siAUzd-neVct")]',
        '//div[@role="main"]',
        '//div[contains(@class, "section-layout")]'
    ]
    
    # Find the scrollable container
    scrollable = None
    for xpath in scrollable_div_xpaths:
        try:
            elements = driver.find_elements(By.XPATH, xpath)
            if elements:
                for element in elements:
                    try:
                        # Check if element is scrollable by examining its properties
                        scroll_height = driver.execute_script("return arguments[0].scrollHeight", element)
                        client_height = driver.execute_script("return arguments[0].clientHeight", element)
                        
                        if scroll_height > client_height:
                            scrollable = element
                            print(f"Found scrollable container with xpath: {xpath}")
                            print(f"Scroll height: {scroll_height}, Client height: {client_height}")
                            break
                    except Exception as e:
                        print(f"Error checking element scrollability: {e}")
                        continue
            if scrollable:
                break
        except Exception:
            continue
    
    if not scrollable:
        print("Could not find scrollable container. Trying direct document scrolling.")
        scrollable = driver.find_element(By.TAG_NAME, 'body')
    
    # Count reviews before scrolling
    review_elements = count_review_elements(driver)
    print(f"Initial review count: {review_elements}")
    
    # Track the last review count to detect when no new reviews are loaded
    last_review_count = 0
    unchanged_count = 0
    scroll_count = 0
    
    # Scroll until we hit maximum or no new reviews load after multiple attempts
    while scroll_count < max_scrolls and unchanged_count < 5:
        try:
            # Try multiple scroll methods
            
            # Method 1: Standard JavaScript scroll
            driver.execute_script("arguments[0].scrollTop = arguments[0].scrollHeight", scrollable)
            print(f"Method 1: Scrolled container, attempt {scroll_count+1}")
            
            # Method 2: Alternative scroll approach
            driver.execute_script("""
                var element = arguments[0];
                element.scrollTo({
                    top: element.scrollHeight,
                    behavior: 'smooth'
                });
            """, scrollable)
            print(f"Method 2: Smooth scrolled container")
            
            # Method 3: Scroll by a specific amount
            driver.execute_script("arguments[0].scrollTop += 1000;", scrollable)
            print(f"Method 3: Incremental scroll by 1000px")
            
            # Method 4: Try to click on the last visible review to ensure focus
            try:
                reviews = driver.find_elements(By.XPATH, '//div[@data-review-id]')
                if reviews:
                    last_review = reviews[-1]
                    driver.execute_script("arguments[0].scrollIntoView({behavior: 'smooth', block: 'end'});", last_review)
                    print(f"Method 4: Scrolled last review into view")
            except Exception as e:
                print(f"Method 4 failed: {e}")
            
            # Method 5: Direct body scroll (a fallback)
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
            print(f"Method 5: Direct body scroll")
            
            # Wait longer for new content to load
            time.sleep(3)
            
            # Count reviews after scrolling
            current_reviews = count_review_elements(driver)
            print(f"Current review count: {current_reviews}")
            
            if current_reviews == last_review_count:
                unchanged_count += 1
                print(f"No new reviews loaded. Unchanged count: {unchanged_count}")
                
                # Take screenshot for debugging if no new reviews loaded
                if unchanged_count == 1:
                    try:
                        screenshot_path = f"scroll_debug_{scroll_count}.png"
                        driver.save_screenshot(screenshot_path)
                        print(f"Saved debug screenshot to {screenshot_path}")
                    except Exception:
                        pass
                        
                # Try to click "Show More Reviews" button if no progress
                try_click_more_reviews(driver)
            else:
                unchanged_count = 0
                print(f"Success! Loaded {current_reviews - last_review_count} new reviews")
            
            last_review_count = current_reviews
            scroll_count += 1
            
        except Exception as e:
            print(f"Error while scrolling: {e}")
            break
    
    final_review_count = count_review_elements(driver)
    print(f"Finished scrolling. Total reviews loaded: {final_review_count}")
    return final_review_count

def try_click_more_reviews(driver):
    """Attempt to click on "More Reviews" or similar buttons."""
    more_reviews_button_xpaths = [
        '//button[contains(text(), "More reviews")]',
        '//button[contains(text(), "Show more")]',
        '//button[contains(@aria-label, "more reviews")]',
        '//button[contains(@aria-label, "Show more reviews")]',
        '//span[contains(text(), "more reviews")]/ancestor::button',
        '//div[contains(text(), "More reviews") and @role="button"]',
        # Add more Google Maps specific selectors
        '//button[contains(@data-tab-index, "0") and contains(text(), "review")]',
        '//button[contains(@class, "HHrUdb")]',  # Common class for buttons in Google Maps
        '//span[text()="More"]/ancestor::button',
        '//div[contains(@jsaction, "pane.review.expandReview")]',
        '//div[text()="Show more reviews"]/ancestor::*[@role="button"]'
    ]
    
    for xpath in more_reviews_button_xpaths:
        try:
            more_buttons = driver.find_elements(By.XPATH, xpath)
            for more_button in more_buttons:
                if more_button.is_displayed():
                    print(f"Found 'More Reviews' button with text: {more_button.text}")
                    try:
                        # Try the regular click first
                        more_button.click()
                        print("Clicked 'More Reviews' button with direct click")
                    except Exception as e:
                        print(f"Direct click failed: {e}, trying JavaScript click")
                        try:
                            # Try JavaScript click as fallback
                            driver.execute_script("arguments[0].click();", more_button)
                            print("Clicked 'More Reviews' button with JavaScript")
                        except Exception as e:
                            print(f"JavaScript click also failed: {e}")
                            continue
                    time.sleep(3)  # Wait longer for new reviews to load
                    return True
        except Exception as e:
            print(f"Error with xpath {xpath}: {e}")
            continue
    
    # Additional fallback method: Look for "more reviews" text and click nearby
    try:
        more_text_elements = driver.find_elements(By.XPATH, '//*[contains(text(), "more review") or contains(text(), "More review")]')
        for el in more_text_elements:
            if el.is_displayed():
                print(f"Found text mentioning more reviews: {el.text}")
                # Click on the element or its parent
                try:
                    el.click()
                    print("Clicked directly on text element")
                except Exception:
                    try:
                        parent = driver.execute_script("return arguments[0].parentNode;", el)
                        driver.execute_script("arguments[0].click();", parent)
                        print("Clicked on parent of text element")
                    except Exception:
                        continue
                time.sleep(3)
                return True
    except Exception as e:
        print(f"Error in fallback method: {e}")
    
    return False

def count_review_elements(driver):
    """Count the number of review elements currently on the page."""
    review_container_xpaths = [
        '//div[contains(@class, "jftiEf")]',
        '//div[contains(@class, "gws-localreviews__google-review")]',
        '//div[contains(@data-review-id, "Ch")]',
        '//div[@data-review-id]',
        '//div[@jsaction="mouseover:pane.review.in"]',
        '//div[starts-with(@class, "m") and contains(@class, "xn")]',
        '//div[contains(@class, "fontBodyMedium")]//div[contains(@class, "MyEned")]',
        '//div[@jscontroller and contains(@class, "fontBodyMedium")]',
        '//*[@class="m6QErb DxyBCb kA9KIf dS8AEf"]//div[@data-review-id and @aria-label]',
        # Add more specific selectors for Google Maps reviews
        '//div[contains(@class, "jJc9Ad")]',
        '//div[contains(@class, "siAUzd-neVct") and @data-review-id]',
        '//div[contains(@aria-label, "reviews") or contains(@aria-label, "review")]'
    ]
    
    max_count = 0
    for xpath in review_container_xpaths:
        try:
            reviews = driver.find_elements(By.XPATH, xpath)
            current_count = len(reviews)
            if current_count > max_count:
                max_count = current_count
                print(f"Found {current_count} reviews with xpath: {xpath}")
        except Exception:
            continue
    
    # If we still can't find reviews, try a more general approach
    if max_count == 0:
        try:
            # Look for elements that might contain reviewer names
            reviewer_elements = driver.find_elements(By.XPATH, '//div[contains(@class, "d4r55") or contains(@class, "DHIhE")]')
            if reviewer_elements:
                max_count = len(reviewer_elements)
                print(f"Found {max_count} possible reviews based on reviewer elements")
        except Exception:
            pass
    
    return max_count

def navigate_to_reviews_tab(driver, url, branch_name=""):
    """
    Navigate to the reviews tab using various methods.
    Returns True if successfully navigated to reviews.
    """
    print(f"\nAttempting to navigate to reviews tab for: {branch_name}")
    
    # First try: Direct navigation via URL modification
    try:
        # Extract place ID from the URL
        match = re.search(r"!1s([^!]+)!", url)
        if match:
            place_id = match.group(1)
            print(f"Extracted place ID: {place_id}")
            
            # Construct a direct URL to the reviews tab
            safe_branch_name = branch_name.replace(' ', '+') if branch_name else "location"
            reviews_url = f"https://www.google.com/maps/place/{safe_branch_name}/@0,0,10z/data=!4m7!3m6!1s{place_id}!8m2!3d0!4d0!9m1!1b1"
            print(f"Navigating directly to reviews URL: {reviews_url}")
            
            driver.get(reviews_url)
            time.sleep(5)  # Wait for the page to load
            
            # Check if we're on a page with reviews
            if count_review_elements(driver) > 0:
                print("Successfully navigated to reviews via URL modification")
                return True
            else:
                print("No reviews found via URL modification, trying alternative methods")
        else:
            print("Could not extract place ID from URL")
    except Exception as e:
        print(f"Error during direct navigation to reviews: {e}")
    
    # Second try: Click on the reviews tab or button
    try:
        # Try various ways to access the reviews section
        wait = WebDriverWait(driver, 15)
        
        # First make sure we're on the main page if URL modification failed
        if not url.endswith("/reviews"):
            driver.get(url)
            time.sleep(5)
        
        # Look for reviews button with various xpaths
        review_button_xpaths = [
            '//button[contains(@aria-label, " reviews")]',
            '//button[contains(@aria-label, "reviews")]',
            '//div[contains(@role, "button")][contains(., "reviews")]',
            '//div[contains(@jsaction, "pane.rating.moreReviews")]',
            '//span[contains(text(), "reviews")]/ancestor::button',
            '//div[contains(@class, "F7nice")]/span[2]/span/span',
            '//button[contains(@jsaction, "pane.rating.moreReviews")]',
            '//button[contains(@data-tab-index, "0") and contains(., "review")]',
            # New patterns specifically for reviews tab
            '//button[@data-tab="reviews" or @data-item-id="reviews"]',
            '//button[contains(@aria-label, "Reviews")]',
            '//div[contains(@role, "tab") and contains(., "review")]'
        ]
        
        for xpath in review_button_xpaths:
            try:
                print(f"Trying to find reviews button with: {xpath}")
                reviews_button = wait.until(EC.element_to_be_clickable((By.XPATH, xpath)))
                print(f"Found reviews button with xpath: {xpath}")
                print(f"Button text: {reviews_button.text}")
                
                # Try to click the button
                try:
                    reviews_button.click()
                    print("Clicked reviews button with direct click")
                except Exception:
                    driver.execute_script("arguments[0].click();", reviews_button)
                    print("Clicked reviews button with JavaScript")
                
                time.sleep(4)
                
                # Check if reviews are visible
                if count_review_elements(driver) > 0:
                    print("Successfully navigated to reviews via button click")
                    return True
                else:
                    print("Clicked button but no reviews found, trying next method")
            except Exception as e:
                print(f"Error with xpath {xpath}: {e}")
                continue
    except Exception as e:
        print(f"Error navigating to reviews tab: {e}")
    
    # Third try: Look for a reviews section that's already visible
    if count_review_elements(driver) > 0:
        print("Reviews already visible on page")
        return True
    
    print("All navigation methods to reviews tab failed")
    return False

def extract_branch_data(driver, url, json_source=""):
    """Extract branch details and reviews from a direct Google Maps branch URL."""
    print(f"\nLoading URL: {url} (source: {json_source})")
    try:
        driver.get(url)
        time.sleep(5)  # Adjust if the page loads slowly
    except Exception as e:
        print(f"Error loading URL: {e}")
        return {
            "name": "Error Loading Page",
            "address": "N/A",
            "rating": "N/A",
            "pincode": "N/A",
            "reviews": [],
            "url": url,
            "source_file": json_source
        }

    # --- Extract Basic Branch Details ---
    branch_name = "Not found"
    address = "Not found"
    rating = "Not found"
    pincode = "Not found"
    
    try:
        branch_name = driver.find_element(By.XPATH, '//h1[contains(@class,"DUwDvf")]').text
        print(f"Found branch name: {branch_name}")
    except Exception as e:
        print(f"Error finding branch name: {e}")
    
    try:
        address = driver.find_element(By.XPATH, '//button[contains(@aria-label, "Address")]/div').text
        print(f"Found address: {address}")
    except Exception as e:
        try:
            # Alternative way to find address
            address_elements = driver.find_elements(By.XPATH, '//div[contains(@class, "Io6YTe")]/div')
            if address_elements:
                address = address_elements[0].text
                print(f"Found address (alternative): {address}")
        except Exception:
            print("Error finding address using both methods")
    
    try:
        rating = driver.find_element(By.XPATH, '//div[contains(@aria-label, " stars")]').get_attribute("aria-label")
        print(f"Found rating: {rating}")
    except Exception as e:
        print(f"Error finding rating: {e}")
        
    if address != "Not found":
        match = re.search(r"\b\d{6}\b", address)
        pincode = match.group(0) if match else "Not found"
    
    print("Branch Name:", branch_name)
    print("Rating:", rating)
    print("Address:", address)
    print("Pincode:", pincode)
    
    # --- Extract Reviews ---
    reviews_list = []
    print("\nFetching reviews for:", branch_name)
    
    # Save a screenshot to debug review issues
    try:
        screenshot_path = os.path.join(BASE_DIR, f"{branch_name}_screenshot.png".replace(" ", "_"))
        driver.save_screenshot(screenshot_path)
        print(f"Saved screenshot to {screenshot_path}")
    except Exception as e:
        print(f"Could not save screenshot: {e}")
    
    # Navigate to the reviews tab
    if navigate_to_reviews_tab(driver, url, branch_name):
        # Successfully navigated to reviews tab
        # Now scroll to load all available reviews
        print("Successfully navigated to reviews tab, now loading all reviews...")
        
        # Scroll to load all reviews
        total_reviews = scroll_to_load_all_reviews(driver, max_scrolls=30)
        print(f"Loaded a total of {total_reviews} reviews")
        
        # Process the reviews
        try:
            # Find parent review containers - these will contain both customer reviews and potentially owner responses
            primary_review_xpaths = [
                '//div[contains(@class, "jftiEf")]',
                '//div[contains(@data-review-id, "Ch")]',
                '//div[@data-review-id]',
                '//div[contains(@class, "fontBodyMedium")]//div[contains(@class, "MyEned")]/ancestor::div[@data-review-id]',
                '//*[@class="m6QErb DxyBCb kA9KIf dS8AEf"]//div[@data-review-id and @aria-label]'
            ]
            
            primary_reviews = []
            for xpath in primary_review_xpaths:
                try:
                    review_elements = driver.find_elements(By.XPATH, xpath)
                    if review_elements and len(review_elements) > 0:
                        primary_reviews = review_elements
                        print(f"Found {len(primary_reviews)} primary review containers with xpath: {xpath}")
                        break
                except Exception as e:
                    print(f"Error with primary review xpath {xpath}: {e}")
            
            # Set max reviews to process (can be adjusted based on need)
            max_reviews_to_process = len(primary_reviews)
            print(f"Processing {max_reviews_to_process} primary review containers...\n")
            
            processed_reviews = 0
            for i, review_container in enumerate(primary_reviews[:max_reviews_to_process]):
                try:
                    # Save individual review HTML for debugging (first few only)
                    if i < 3:
                        try:
                            review_html = review_container.get_attribute('outerHTML')
                            review_debug_path = os.path.join(BASE_DIR, f"{branch_name}_review_{i+1}_debug.txt".replace(" ", "_"))
                            with open(review_debug_path, 'w', encoding='utf-8') as f:
                                f.write(review_html)
                            print(f"Saved review {i+1} HTML to {review_debug_path}")
                        except Exception:
                            pass
                    
                    # IMPORTANT: First check if this entire container is an owner response
                    is_full_container_owner_response = False
                    try:
                        # Look for indicators that the entire container is an owner response
                        owner_container_indicators = [
                            './/div[contains(text(), "Response from the owner")]',
                            './/div[contains(@class, "CDe7pd")][contains(text(), "owner")]',
                            './/div[contains(text(), "Owner response")]',
                            './/div[contains(@class, "JsEyr")][contains(text(), "owner")]',
                            './/div[@jslog and contains(text(), "owner")]'
                        ]
                        
                        for xpath in owner_container_indicators:
                            owner_indicators = review_container.find_elements(By.XPATH, xpath)
                            if owner_indicators and len(owner_indicators) > 0:
                                print(f"Container {i+1} is an owner response - skipping")
                                is_full_container_owner_response = True
                                break
                    except Exception as e:
                        print(f"Error checking if container {i+1} is owner response: {e}")
                    
                    if is_full_container_owner_response:
                        continue
                    
                    # Process customer review within this container
                    # First, identify the reviewer information
                    reviewer = "Unknown Reviewer"
                    reviewer_xpaths = [
                        './/div[contains(@class, "d4r55")]',
                        './/div[@class="TSUbDb"]',
                        './/div[contains(@class, "WNxzHc")]',
                        './/div[contains(@class, "tPuDnb")]',
                        './/span[@class="x3AX1-LfntMc-header-title-title"]/span',
                        './/div[@class="DHIhE"]',
                        './/div[@role="text" and @class]',
                        './/a[contains(@href, "contrib")]',
                        './/div[contains(@class, "WNxzHc")]//span'
                    ]
                    
                    for xpath in reviewer_xpaths:
                        try:
                            reviewer_elements = review_container.find_elements(By.XPATH, xpath)
                            if reviewer_elements and reviewer_elements[0].text and len(reviewer_elements[0].text) > 0:
                                reviewer = reviewer_elements[0].text
                                break
                        except Exception:
                            continue
                    
                    # Skip if reviewer name indicates this is the owner
                    if (reviewer.lower() == "owner" or 
                        "owner" in reviewer.lower() or 
                        (branch_name != "Not found" and branch_name.lower() in reviewer.lower())):
                        print(f"Skipping review {i+1} as reviewer '{reviewer}' appears to be the owner")
                        continue
                    
                    # Expand the review if it's truncated
                    try:
                        more_button_xpaths = [
                            './/button[@aria-label="More"]',
                            './/button[contains(text(), "More")]',
                            './/button[contains(@class, "w8nwRe")]',
                            './/button[text()="More"]',
                            './/button[contains(@jsaction, "pane.review.expandReview")]'
                        ]
                        
                        for xpath in more_button_xpaths:
                            more_buttons = review_container.find_elements(By.XPATH, xpath)
                            for more_button in more_buttons:
                                if more_button.is_displayed():
                                    try:
                                        more_button.click()
                                    except Exception:
                                        driver.execute_script("arguments[0].click();", more_button)
                                    print(f"Expanded review {i+1}")
                                    time.sleep(0.5)
                                    break
                    except Exception as e:
                        print(f"Error expanding review {i+1}: {e}")
                    
                    # Get review text - focus on the main customer review, not the owner response
                    review_text = "No review text found"
                    text_xpaths = [
                        './/span[contains(@class, "wiI7pd")]',
                        './/div[contains(@class, "wiI7pd")]',
                        './/*[contains(@class, "MyEned")]',
                        './/*[contains(@class, "review-full-text")]',
                        './/span[contains(@class, "review-full-text")]',
                        './/div[@class="MyEned"]',
                        './/div[@data-js-log-root]',
                        './/div[contains(@class, "RBcccd")]/div[not(contains(@class, "CDe7pd"))]/span',
                        './/div[contains(@class, "RBcccd")]/div[not(contains(@class, "CDe7pd"))]/div'
                    ]
                    
                    # First try to find actual review text containers that are not owner responses
                    for xpath in text_xpaths:
                        try:
                            # Get all potential text elements
                            text_elements = review_container.find_elements(By.XPATH, xpath)
                            
                            # Filter out elements that are inside owner response sections
                            filtered_elements = []
                            for element in text_elements:
                                # Check if this element is inside an owner response section
                                parent_is_owner = False
                                try:
                                    # Check if any parent element has owner response indicators
                                    owner_indicators = element.find_elements(By.XPATH, 'ancestor::div[contains(text(), "Response from the owner") or contains(@class, "CDe7pd") or contains(text(), "Owner response")]')
                                    if owner_indicators and len(owner_indicators) > 0:
                                        parent_is_owner = True
                                except Exception:
                                    pass
                                
                                if not parent_is_owner and element.text and len(element.text) > 0:
                                    filtered_elements.append(element)
                            
                            # Use the first valid text element
                            if filtered_elements:
                                review_text = filtered_elements[0].text
                                break
                        except Exception:
                            continue
                    
                    # Get review rating
                    review_rating = "Rating not found"
                    rating_xpaths = [
                        './/span[contains(@aria-label, "stars")]',
                        './/*[contains(@class, "kvMYJc")]',
                        './/*[contains(@aria-label, "Rated")]',
                        './/div[@role="img" and contains(@aria-label, "stars")]',
                        './/g-review-stars',
                        './/*[contains(@class, "IQDGvf")]',
                        './/span[@role="img"]'
                    ]
                    
                    for xpath in rating_xpaths:
                        try:
                            rating_elements = review_container.find_elements(By.XPATH, xpath)
                            if rating_elements:
                                aria_label = rating_elements[0].get_attribute('aria-label')
                                if aria_label and "star" in aria_label.lower():
                                    review_rating = aria_label
                                    break
                                
                                # If no aria-label, try looking at class name indicators
                                class_attr = rating_elements[0].get_attribute('class')
                                if class_attr and any(c in class_attr for c in ['kvMYJc', 'IQDGvf']):
                                    # Try to extract rating from style attribute
                                    style_attr = rating_elements[0].get_attribute('style')
                                    if style_attr and 'width' in style_attr:
                                        width_match = re.search(r'width:\s*(\d+)%', style_attr)
                                        if width_match:
                                            width_percent = int(width_match.group(1))
                                            stars = round(width_percent / 20, 1)
                                            review_rating = f"{stars} stars"
                                            break
                        except Exception:
                            continue
                    
                    # Get review date
                    review_date = "Date not found"
                    date_xpaths = [
                        './/span[contains(@class, "rsqaWe")]',
                        './/span[contains(@class, "dehysf")]',
                        './/span[contains(@class, "ODSEW-ShBeI-RgZmSc-date")]',
                        './/span[contains(@class, "review-date")]',
                        './/div[contains(@class, "DHIhE")]/following-sibling::div',
                        './/div[contains(@class, "DU9Pgb")]/span'
                    ]
                    
                    for xpath in date_xpaths:
                        try:
                            date_elements = review_container.find_elements(By.XPATH, xpath)
                            if date_elements and date_elements[0].text and len(date_elements[0].text) > 0:
                                review_date = date_elements[0].text
                                break
                        except Exception:
                            continue
                    
                    # Look for bank response to this review (if any)
                    owner_response = "No response from bank"
                    try:
                        response_container_xpaths = [
                            './/div[contains(text(), "Response from the owner")]/following-sibling::div',
                            './/div[contains(@class, "CDe7pd")]/following-sibling::div',
                            './/div[contains(text(), "Owner response")]/following-sibling::div',
                            './/div[contains(@class, "JsEyr")]/following-sibling::div'
                        ]
                        
                        for xpath in response_container_xpaths:
                            response_elements = review_container.find_elements(By.XPATH, xpath)
                            if response_elements and response_elements[0].text and len(response_elements[0].text) > 0:
                                owner_response = response_elements[0].text
                                break
                    except Exception as e:
                        print(f"Error finding owner response for review {i+1}: {e}")
                    
                    # Add the review to our list
                    review_data = {
                        "reviewer": reviewer,
                        "rating": review_rating,
                        "date": review_date,
                        "text": review_text,
                        "bank_response": owner_response
                    }
                    
                    reviews_list.append(review_data)
                    processed_reviews += 1
                    print(f"Processed review {i+1}: {reviewer} - {review_rating} ({review_date})")
                    
                except StaleElementReferenceException:
                    print(f"Stale element reference for review {i+1}. Skipping.")
                except Exception as e:
                    print(f"Error processing review {i+1}: {e}")
            
            print(f"\nSuccessfully extracted {processed_reviews} reviews")
        except Exception as e:
            print(f"Error processing reviews: {e}")
    else:
        print("Could not navigate to reviews tab, no reviews extracted")
    
    # Compile all data
    branch_data = {
        "name": branch_name,
        "address": address,
        "rating": rating,
        "pincode": pincode,
        "reviews": reviews_list,
        "url": url,
        "source_file": json_source
    }
    
    return branch_data

def process_all_branches(json_files, branches_per_file=None, max_branches_total=None):
    """Process branches from all JSON files."""
    all_branch_data = []
    processed_count = 0
    
    # Set up WebDriver
    options = webdriver.ChromeOptions()
    options.add_argument("--window-size=1920,1080")
    options.add_argument("--disable-gpu")
    options.add_argument("--disable-extensions")
    options.add_argument("--disable-notifications")
    options.add_experimental_option("prefs", {
        "profile.default_content_setting_values.notifications": 2
    })
    
    # Uncomment to run in headless mode
    # options.add_argument("--headless")
    
    driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
    
    try:
        for json_file in json_files:
            json_basename = os.path.basename(json_file)
            print(f"\n{'='*50}")
            print(f"Processing JSON file: {json_basename}")
            print(f"{'='*50}")
            
            # Load branch URLs from the current JSON file
            branch_urls = load_branch_urls_from_file(json_file, limit=branches_per_file)
            
            # Create output directory for this state if it doesn't exist
            state_name = os.path.splitext(json_basename)[0].replace("uco_bank_", "")
            output_dir = os.path.join(BASE_DIR, "extracted_data", state_name)
            os.makedirs(output_dir, exist_ok=True)
            
            # Process each branch URL
            for i, url in enumerate(branch_urls):
                if max_branches_total is not None and processed_count >= max_branches_total:
                    print(f"Reached maximum total branches limit ({max_branches_total}). Stopping.")
                    break
                
                print(f"\nProcessing branch {i+1}/{len(branch_urls)} from {json_basename}")
                try:
                    branch_data = extract_branch_data(driver, url, json_source=json_basename)
                    
                    # Save individual branch data to JSON file
                    branch_slug = branch_data['name'].lower().replace(' ', '_').replace(',', '').replace('/', '_')[:30]
                    if branch_slug == "not_found":
                        branch_slug = f"unknown_branch_{i+1}"
                    
                    branch_file = os.path.join(output_dir, f"{branch_slug}.json")
                    
                    with open(branch_file, 'w', encoding='utf-8') as f:
                        json.dump(branch_data, f, indent=2, ensure_ascii=False)
                    
                    print(f"Saved branch data to {branch_file}")
                    
                    # Add to overall collection
                    all_branch_data.append(branch_data)
                    processed_count += 1
                    
                except Exception as e:
                    print(f"Error processing branch {i+1}: {e}")
                
                # Add a delay between branches to avoid being rate-limited
                time.sleep(3)
            
            # Save combined data for this state
            if all_branch_data:
                combined_file = os.path.join(output_dir, f"{state_name}_all_branches.json")
                with open(combined_file, 'w', encoding='utf-8') as f:
                    json.dump(all_branch_data, f, indent=2, ensure_ascii=False)
                print(f"Saved combined data for {state_name} to {combined_file}")
            
            # Add a delay between files to avoid being rate-limited
            time.sleep(5)
            
    finally:
        driver.quit()
    
    return all_branch_data

def main():
    """Main function to run the scraping process."""
    print("Starting UCO Bank review scraping process...")
    
    # Check if BASE_DIR exists
    if not os.path.exists(BASE_DIR):
        print(f"Error: Base directory {BASE_DIR} does not exist.")
        return
    
    # Check if JSON_FOLDER exists
    if not os.path.exists(JSON_FOLDER):
        print(f"Error: JSON folder {JSON_FOLDER} does not exist.")
        return
    
    # Create output directory if it doesn't exist
    output_dir = os.path.join(BASE_DIR, "extracted_data")
    os.makedirs(output_dir, exist_ok=True)
    
    # Get all JSON files
    json_files = get_all_json_files()
    
    if not json_files:
        print("No JSON files found. Exiting.")
        return
    
    print(f"Found {len(json_files)} JSON files.")
    
    # For testing, you can limit the number of branches per file and total
    # Set to None to process all branches
    branches_per_file = 5  # Process only first 5 branches per file for testing
    max_branches_total = 30  # Process a maximum of 30 branches in total
    
    # For production, set these to None to process all branches
    # branches_per_file = None
    # max_branches_total = None
    
    # Process all branches
    all_branch_data = process_all_branches(json_files, branches_per_file, max_branches_total)
    
    # Save all data to a single combined file
    if all_branch_data:
        combined_file = os.path.join(output_dir, "all_branches_combined.json")
        with open(combined_file, 'w', encoding='utf-8') as f:
            json.dump(all_branch_data, f, indent=2, ensure_ascii=False)
        print(f"\nSaved all combined data to {combined_file}")
        
        # Create a pandas DataFrame and export to CSV
        try:
            # Flatten the data structure for CSV
            flattened_data = []
            for branch in all_branch_data:
                branch_info = {
                    "name": branch["name"],
                    "address": branch["address"],
                    "rating": branch["rating"],
                    "pincode": branch["pincode"],
                    "url": branch["url"],
                    "source_file": branch["source_file"],
                    "review_count": len(branch["reviews"])
                }
                
                # Add branch with no reviews
                if not branch["reviews"]:
                    branch_info["reviewer"] = "No reviews"
                    branch_info["review_rating"] = "N/A"
                    branch_info["review_date"] = "N/A"
                    branch_info["review_text"] = "N/A"
                    branch_info["bank_response"] = "N/A"
                    flattened_data.append(branch_info)
                else:
                    # Add each review as a separate row
                    for review in branch["reviews"]:
                        review_info = branch_info.copy()
                        review_info["reviewer"] = review["reviewer"]
                        review_info["review_rating"] = review["rating"]
                        review_info["review_date"] = review["date"]
                        review_info["review_text"] = review["text"]
                        review_info["bank_response"] = review["bank_response"]
                        flattened_data.append(review_info)
            
            # Create DataFrame and export to CSV
            df = pd.DataFrame(flattened_data)
            csv_file = os.path.join(output_dir, "all_branches_reviews.csv")
            df.to_csv(csv_file, index=False, encoding='utf-8-sig')
            print(f"Exported data to CSV: {csv_file}")
            
        except Exception as e:
            print(f"Error creating CSV export: {e}")
    
    print("\nScraping process completed.")

if __name__ == "__main__":
    main()

# Sentiment Analysis on Google review


In [20]:
import pandas as pd
import numpy as np
import unicodedata
import torch
import logging
import os
import re
from tqdm import tqdm
from sentence_transformers import SentenceTransformer, util
from transformers import AutoTokenizer, AutoModelForSequenceClassification, AutoModelForSeq2SeqLM
from langdetect import detect, LangDetectException

# ------------------ Setup Logging ------------------
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s'
)
logger = logging.getLogger(__name__)

# ------------------ Paths ------------------
INPUT_FILE_PATH = r"C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping\extracted_data\all_branches_reviews.csv"
TOPICS_FILE_PATH = r"C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping\Sentiment_analysis\topic_categorisation.txt"
OUTPUT_FILE_PATH = r"C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping\Sentiment_analysis\reviews_sentiment_topic.csv"

# ------------------ Create Output Directory ------------------
output_dir = os.path.dirname(OUTPUT_FILE_PATH)
if not os.path.exists(output_dir):
    os.makedirs(output_dir)
    logger.info(f"📁 Created output directory: {output_dir}")

# ------------------ Create Topics File ------------------
def create_topics_file():
    """Create a topics file for bank reviews if it doesn't exist"""
    if os.path.exists(TOPICS_FILE_PATH):
        return
    
    # Define banking-specific topics with examples
    topics_dict = {
        "Customer Service": [
            "The staff was very helpful and polite",
            "I had a terrible experience with their customer service",
            "The bank employees were knowledgeable and solved my problem quickly",
            "Nobody answered my queries properly",
            "Service is excellent and staff is friendly"
        ],
        "Account Management": [
            "Opening an account was easy and quick",
            "Had issues with my account balance",
            "The process to update my KYC was smooth",
            "My account was debited without authorization",
            "The online banking system is user-friendly"
        ],
        "Loan Processing": [
            "My loan was approved quickly",
            "The interest rates are too high",
            "The loan documentation process was tedious",
            "They rejected my loan application without explanation",
            "Affordable EMI options for home loans"
        ],
        "Digital Banking": [
            "The mobile app is convenient to use",
            "Online banking platform needs improvement",
            "The app keeps crashing when I try to transfer money",
            "Internet banking is secure and fast",
            "The UPI payment feature works flawlessly"
        ],
        "Branch Facilities": [
            "The branch is clean and well-maintained",
            "Not enough cash counters during peak hours",
            "ATM is always out of service",
            "The branch location is convenient",
            "Long waiting times at the branch"
        ],
        "Charges & Fees": [
            "The bank charges too many hidden fees",
            "Reasonable service charges compared to other banks",
            "High maintenance charges for savings account",
            "They waived the annual credit card fee",
            "Excessive penalties for minimum balance requirements"
        ],
        "General Feedback": [
            "Overall a good bank",
            "I recommend this bank to everyone",
            "Worst banking experience ever",
            "The bank has improved a lot in recent years",
            "Better than other banks in the area"
        ]
    }
    
    topics_dir = os.path.dirname(TOPICS_FILE_PATH)
    if not os.path.exists(topics_dir):
        os.makedirs(topics_dir)
    
    with open(TOPICS_FILE_PATH, 'w', encoding='utf-8') as f:
        f.write("Bank Review Topics Dictionary:\n\n")
        f.write(str(topics_dict))
    
    logger.info(f"📝 Created topics file at: {TOPICS_FILE_PATH}")
    return topics_dict

# ------------------ Load Topics ------------------
def load_topics_from_file(file_path):
    if not os.path.exists(file_path):
        return create_topics_file()
    
    with open(file_path, 'r', encoding='utf-8') as file:
        content = file.read()
        dict_start = content.find('{')
        dict_end = content.rfind('}') + 1
        dict_content = content[dict_start:dict_end]
        topics_dict = eval(dict_content)
    return topics_dict

# ------------------ Load Data ------------------
def load_data(file_path):
    encodings_to_try = ['utf-8-sig', 'utf-8', 'ISO-8859-1']
    for enc in encodings_to_try:
        try:
            with open(file_path, 'r', encoding=enc, errors='replace') as f:
                df = pd.read_csv(f)
            logger.info(f"✅ Loaded CSV using encoding: {enc}")
            break
        except UnicodeDecodeError:
            logger.warning(f"⚠️ Failed to load with encoding: {enc}")
    else:
        raise UnicodeDecodeError("❌ Unable to decode file using tried encodings.")

    df.drop_duplicates(inplace=True)
    df.columns = [col.lower().strip() for col in df.columns]
    
    # Ensure we have the required columns
    required_columns = ['address', 'url', 'reviewer', 'review_rating', 'review_text']
    for col in required_columns:
        if col not in df.columns:
            raise ValueError(f"Required column '{col}' not found in the CSV file")
    
    # Clean and prepare data
    df['review_text'] = df['review_text'].astype(str).fillna("")
    
    return df

# ------------------ Topic Embeddings ------------------
def compute_all_example_embeddings(model, topics_dict):
    topic_examples = []
    topic_labels = []
    for topic, examples in topics_dict.items():
        for example in examples:
            topic_examples.append(example)
            topic_labels.append(topic)

    logger.info(f"🧠 Encoding {len(topic_examples)} topic examples...")
    example_embeddings = model.encode(topic_examples, batch_size=32, convert_to_tensor=True)
    return topic_examples, topic_labels, example_embeddings

def match_comment_to_topic(comment, model, topic_labels, example_embeddings, threshold=0.6):
    if not comment.strip():
        return "Other / Unclassified", 0.0

    comment_embedding = model.encode(comment, convert_to_tensor=True)
    cos_scores = util.cos_sim(comment_embedding, example_embeddings)[0]
    top_index = torch.argmax(cos_scores).item()
    top_score = cos_scores[top_index].item()

    if top_score >= threshold:
        return topic_labels[top_index], round(top_score, 3)
    else:
        return "Other / Unclassified", round(top_score, 3)

# ------------------ Text Normalization & Cleanup ------------------
def normalize_text(text):
    """Normalize Unicode characters to NFC form"""
    return unicodedata.normalize("NFC", text) if isinstance(text, str) else ""

def clean_translation(text):
    """Clean up common translation artifacts"""
    if not isinstance(text, str):
        return ""
    
    # Remove excessive spaces
    text = re.sub(r'\s+', ' ', text).strip()
    
    # Fix common artifacts
    text = re.sub(r'\.{2,}', '...', text)  # Standardize ellipses
    text = re.sub(r'�', '', text)  # Remove replacement character
    text = re.sub(r'\( *\)', '', text)  # Remove empty parentheses
    text = re.sub(r'\[ *\]', '', text)  # Remove empty brackets
    text = re.sub(r'\s+([.,!?;:])', r'\1', text)  # Fix spacing before punctuation
    
    # Fix double punctuation
    text = re.sub(r'([.,!?;:]){2,}', r'\1', text)
    
    return text.strip()

# ------------------ Script Detection ------------------
SCRIPT_PATTERNS = {
    'bengali': r'[\u0980-\u09FF\u09BC\u09BE-\u09CC\u09CD\u09D7]',
    'devanagari': r'[\u0900-\u097F\uA8E0-\uA8FF\u1CD0-\u1CFF]',
    'gurmukhi': r'[\u0A00-\u0A7F]',
    'gujarati': r'[\u0A80-\u0AFF]',
    'oriya': r'[\u0B00-\u0B7F]',
    'tamil': r'[\u0B80-\u0BFF]',
    'telugu': r'[\u0C00-\u0C7F]',
    'kannada': r'[\u0C80-\u0CFF]',
    'malayalam': r'[\u0D00-\u0D7F]'
}

def detect_scripts(text):
    """Detect all scripts present in text"""
    if not isinstance(text, str) or not text.strip():
        return set()
    
    detected_scripts = set()
    for script, pattern in SCRIPT_PATTERNS.items():
        if re.search(pattern, text):
            detected_scripts.add(script)
            
    # Check for Latin script (English/Roman letters)
    if re.search(r'[a-zA-Z]', text):
        detected_scripts.add('latin')
        
    return detected_scripts

def get_primary_script(text):
    """Get the primary script used in text"""
    scripts = detect_scripts(text)
    
    # No script detected
    if not scripts:
        return 'unknown'
    
    # Find the script with the most characters
    script_counts = {}
    for script in scripts:
        if script == 'latin':
            script_counts[script] = len(re.findall(r'[a-zA-Z]', text))
        else:
            pattern = SCRIPT_PATTERNS.get(script, '')
            script_counts[script] = len(re.findall(pattern, text))
    
    primary_script = max(script_counts.items(), key=lambda x: x[1])[0]
    return primary_script

# ------------------ Language Detection with Script Awareness ------------------
SCRIPT_TO_LANG = {
    'devanagari': 'hi',  # Hindi
    'bengali': 'bn',     # Bengali
    'tamil': 'ta',       # Tamil
    'telugu': 'te',      # Telugu
    'kannada': 'kn',     # Kannada
    'malayalam': 'ml',   # Malayalam
    'gurmukhi': 'pa',    # Punjabi
    'gujarati': 'gu',    # Gujarati
    'oriya': 'or',       # Oriya/Odia
}

def detect_lang(text):
    """Detect language with script awareness and fallbacks"""
    if not isinstance(text, str) or not text.strip():
        return 'unknown'
    
    # Get primary script 
    primary_script = get_primary_script(text)
    
    # If it's a known Indian script, use the script for language detection
    if primary_script in SCRIPT_TO_LANG:
        return SCRIPT_TO_LANG[primary_script]
    
    # Try langdetect for latin script or mixed text
    try:
        # For mixed scripts containing Indian language in Latin script
        if 'latin' in detect_scripts(text) and len(detect_scripts(text)) > 1:
            # Check for common Hindi/Indian words in Latin script
            common_indian_words = ['namaste', 'acha', 'theek', 'bahut', 'kadam', 'shubh', 'desi', 
                                   'dhan', 'dhanyavad', 'namaskar', 'shukriya']
            
            text_lower = text.lower()
            for word in common_indian_words:
                if word in text_lower:
                    logger.info(f"🔍 Detected Hindi-in-Latin: '{word}' in '{text[:50]}...'")
                    return 'hi'  # Treat as Hindi written in Latin script
        
        # Fall back to regular language detection
        return detect(text)
    except LangDetectException:
        return 'unknown'

# ------------------ Enhanced Translation ------------------
LANG_MAP = {
    'hi': 'hin_Deva',  # Hindi
    'bn': 'ben_Beng',  # Bengali
    'ta': 'tam_Taml',  # Tamil
    'te': 'tel_Telu',  # Telugu
    'ml': 'mal_Mlym',  # Malayalam
    'gu': 'guj_Gujr',  # Gujarati
    'kn': 'kan_Knda',  # Kannada
    'mr': 'mar_Deva',  # Marathi
    'pa': 'pan_Guru',  # Punjabi
    'or': 'ory_Orya',  # Odia/Oriya
    'en': 'eng_Latn',  # English
    'ur': 'urd_Arab',  # Urdu
    'unknown': 'eng_Latn',  # Default to English for unknown
}

def preprocess_mixed_script(text):
    """Handle mixed script text, especially Hindi written in Latin"""
    scripts = detect_scripts(text)
    
    # If multiple scripts including Latin and an Indian script
    if len(scripts) > 1 and 'latin' in scripts:
        # For now, just log the detection - more complex handling could be added later
        logger.info(f"🔄 Mixed script text detected: '{text[:50]}...'")
    
    return text

def batch_translate(comments, tokenizer, model, batch_size=16):
    """Translate comments in batches for efficiency"""
    all_translations = []
    
    # Process in batches
    for i in range(0, len(comments), batch_size):
        batch = comments[i:i+batch_size]
        batch_translations = []
        
        # Preprocess and determine language for each comment in batch
        preprocessed_batch = []
        src_langs = []
        
        for comment in batch:
            comment = normalize_text(comment)
            comment = preprocess_mixed_script(comment)
            lang = detect_lang(comment)
            
            preprocessed_batch.append(comment)
            src_langs.append(lang)
        
        # Translate each comment in batch
        for j, (comment, lang) in enumerate(zip(preprocessed_batch, src_langs)):
            if lang == 'en' or not comment.strip():
                batch_translations.append(comment)
                continue
                
            src_lang_code = LANG_MAP.get(lang, 'eng_Latn')
            tgt_lang_code = 'eng_Latn'
            
            try:
                tokenizer.src_lang = src_lang_code
                inputs = tokenizer(comment, return_tensors="pt", truncation=True, max_length=512)
                
                translated_tokens = model.generate(
                    **inputs,
                    forced_bos_token_id = tokenizer(tgt_lang_code, add_special_tokens=False).input_ids[0],
                    max_length=512,
                    num_beams=5,
                    early_stopping=True
                )
                
                translated = tokenizer.batch_decode(translated_tokens, skip_special_tokens=True)[0].strip()
                translated = clean_translation(translated)
                
                if not translated or "�" in translated:
                    logger.warning(f"⚠️ Bad translation output for '{comment[:30]}...' from {lang}")
                    batch_translations.append(comment)  # Fall back to original
                else:
                    batch_translations.append(translated)
                    
            except Exception as e:
                logger.warning(f"❌ Translation failed: {type(e).__name__}: {str(e)[:100]}")
                batch_translations.append(comment)  # Fall back to original
        
        all_translations.extend(batch_translations)
    
    return all_translations

# ------------------ Sentiment Analysis ------------------
import string
import re
import torch

# Known placeholder texts - define once here
placeholder_texts = {
    "", "no review", "no review text", "no review text found", "n/a", "none", ".", "-", "not available", "not given"
}

def clean_and_normalize(text):
    """Clean and normalize review text."""
    if not isinstance(text, str):
        return ""
    text = text.replace('\r', '').replace('\n', '').replace('\xa0', ' ')
    text = text.lower().strip()
    text = ''.join(ch for ch in text if ch in string.printable)
    return " ".join(text.split())

def batch_analyze_sentiment(texts, ratings, tokenizer, model, batch_size=32):
    """
    Analyze sentiment using review text and rating together.
    If text is missing or placeholder, fallback to rating alone.
    When text sentiment conflicts with rating, prioritize high-confidence text sentiment.
    """
    results = []

    def extract_rating(r):
        """Extract numeric rating from string like '5 stars'. Returns int or 0."""
        try:
            return int(re.search(r'\d+', str(r)).group())
        except:
            return 0

    for i in range(0, len(texts), batch_size):
        batch_texts = texts[i:i+batch_size]
        batch_ratings_raw = ratings[i:i+batch_size]

        batch_ratings = [extract_rating(r) for r in batch_ratings_raw]

        sentiments = ['neutral'] * len(batch_texts)
        scores = [0.0] * len(batch_texts)

        valid_texts = []
        valid_indices = []

        for j, text in enumerate(batch_texts):
            clean_text = clean_and_normalize(text)
            rating = batch_ratings[j]

            if clean_text in placeholder_texts:
                # If review text is placeholder or empty, use rating only
                if rating in [1, 2]:
                    sentiments[j] = 'negative'
                    scores[j] = 1.0
                elif rating == 3:
                    sentiments[j] = 'neutral'
                    scores[j] = 1.0
                elif rating in [4, 5]:
                    sentiments[j] = 'positive'
                    scores[j] = 1.0
                else:
                    sentiments[j] = 'neutral'
                    scores[j] = 0.0
            else:
                valid_texts.append(clean_text)
                valid_indices.append(j)

        if valid_texts:
            inputs = tokenizer(valid_texts, return_tensors='pt', truncation=True,
                               padding=True, max_length=512)
            with torch.no_grad():
                outputs = model(**inputs)
            probs = torch.nn.functional.softmax(outputs.logits, dim=1)
            max_indices = torch.argmax(probs, dim=1)
            sentiment_labels = ['negative', 'neutral', 'positive']

            for idx, valid_idx in enumerate(valid_indices):
                sentiment_idx = max_indices[idx].item()
                confidence = round(probs[idx, sentiment_idx].item(), 3)
                sentiment = sentiment_labels[sentiment_idx]
                rating = batch_ratings[valid_idx]

                # Adjust sentiment if rating and text sentiment conflict
                if sentiment == 'neutral':
                    if rating in [1, 2]:
                        sentiment = 'negative'
                        confidence = max(confidence, 0.7)
                    elif rating in [4, 5]:
                        sentiment = 'positive'
                        confidence = max(confidence, 0.7)
                elif (sentiment == 'positive' and rating in [1, 2]) or (sentiment == 'negative' and rating in [4, 5]):
                    if confidence > 0.75:
                        confidence = max(confidence, 0.85)
                    else:
                        sentiment = 'neutral'
                        confidence = 0.6

                sentiments[valid_idx] = sentiment
                scores[valid_idx] = confidence

        results.extend(zip(sentiments, scores))

    return results





# ------------------ Main ------------------
def main():
    device = 'cuda' if torch.cuda.is_available() else 'cpu'
    logger.info(f"🚀 Starting bank review sentiment analysis using device: {device}")

    # Load models
    logger.info("📚 Loading models...")
    topic_model = SentenceTransformer('all-MiniLM-L6-v2').to(device)
    
    logger.info("📚 Loading translation model (NLLB-200-distilled-600M)...")
    translation_tokenizer = AutoTokenizer.from_pretrained("facebook/nllb-200-distilled-600M")
    translation_model = AutoModelForSeq2SeqLM.from_pretrained("facebook/nllb-200-distilled-600M")
    
    logger.info("📚 Loading sentiment model...")
    sentiment_tokenizer = AutoTokenizer.from_pretrained("cardiffnlp/twitter-xlm-roberta-base-sentiment")
    sentiment_model = AutoModelForSequenceClassification.from_pretrained("cardiffnlp/twitter-xlm-roberta-base-sentiment")

    # Load topics & data
    logger.info("📂 Loading topics and data...")
    topics_dict = load_topics_from_file(TOPICS_FILE_PATH)
    topic_examples, topic_labels, example_embeddings = compute_all_example_embeddings(
        topic_model, topics_dict
    )
    df = load_data(INPUT_FILE_PATH)

    # Extract reviews
    reviews = df['review_text'].tolist()
    total_reviews = len(reviews)
    logger.info(f"📦 Processing {total_reviews} reviews...")

    # Step 1: Translate reviews in batches
    logger.info("🔄 Translating reviews in batches...")
    translated_reviews = batch_translate(
        reviews, translation_tokenizer, translation_model, batch_size=16
    )
    
    # Step 2: Analyze sentiment in batches
    logger.info("😊 Analyzing sentiment in batches...")
    sentiment_results = batch_analyze_sentiment(
    translated_reviews, df['review_rating'].tolist(), sentiment_tokenizer, sentiment_model, batch_size=32
    )

    
    # Step 3: Match reviews to topics
    logger.info("🏷️ Categorizing topics...")
    topic_results = []
    for translated in tqdm(translated_reviews, desc="Matching topics"):
        topic, topic_score = match_comment_to_topic(
            translated, topic_model, topic_labels, example_embeddings, threshold=0.6
        )
        topic_results.append((topic, topic_score))
    
    # Combine results into dataframe
    logger.info("🔄 Combining results...")
    # Only keep the required columns from the original dataframe
    selected_cols = ['address', 'url', 'reviewer', 'review_rating', 'review_text']
    result_df = df[selected_cols].copy()
    
    # Add the analysis results
    result_df['translated_review'] = translated_reviews
    result_df['topic_categorisation'] = [tr[0] for tr in topic_results]
    result_df['topic_confidence'] = [tr[1] for tr in topic_results]
    result_df['sentiment'] = [sr[0] for sr in sentiment_results]
    result_df['sentiment_score'] = [sr[1] for sr in sentiment_results]
    
    # Save results
    result_df.to_csv(OUTPUT_FILE_PATH, index=False, encoding='utf-8-sig')
    logger.info(f"✨ Final output saved to: {OUTPUT_FILE_PATH} (UTF-8 with BOM)")
    
    # Print summary
    logger.info("📊 Processing Summary:")
    logger.info(f"   - Total reviews processed: {total_reviews}")
    logger.info(f"   - Topic distribution: {result_df['topic_categorisation'].value_counts().to_dict()}")
    logger.info(f"   - Sentiment distribution: {result_df['sentiment'].value_counts().to_dict()}")

if __name__ == "__main__":
    main()

2025-05-15 14:27:07,457 - INFO - 🚀 Starting bank review sentiment analysis using device: cpu
2025-05-15 14:27:07,458 - INFO - 📚 Loading models...
2025-05-15 14:27:07,471 - INFO - Use pytorch device_name: cpu
2025-05-15 14:27:07,478 - INFO - Load pretrained SentenceTransformer: all-MiniLM-L6-v2
2025-05-15 14:27:11,333 - INFO - 📚 Loading translation model (NLLB-200-distilled-600M)...
2025-05-15 14:27:22,404 - INFO - 📚 Loading sentiment model...
2025-05-15 14:27:34,417 - INFO - 📂 Loading topics and data...
2025-05-15 14:27:34,423 - INFO - 🧠 Encoding 209 topic examples...


Batches:   0%|          | 0/7 [00:00<?, ?it/s]

2025-05-15 14:27:36,644 - INFO - ✅ Loaded CSV using encoding: utf-8-sig
2025-05-15 14:27:36,768 - INFO - 📦 Processing 19641 reviews...
2025-05-15 14:27:36,770 - INFO - 🔄 Translating reviews in batches...
2025-05-15 14:40:42,843 - INFO - 🔄 Mixed script text detected: 'गुड बैंक गुड शाखा गुड ब्रांच hai and I was in my e...'
2025-05-15 15:09:52,933 - INFO - 🔄 Mixed script text detected: 'All over staf GOOd but Passbook entry in after 3:3...'
2025-05-15 15:16:07,936 - INFO - 🔄 Mixed script text detected: 'UCO बैंक...'
2025-05-15 15:36:24,338 - INFO - 🔄 Mixed script text detected: 'UCO Bank हिनू शाखा,...'
2025-05-15 15:50:21,920 - INFO - 🔄 Mixed script text detected: 'Very good सॉल्यूशन uco m banking digital banking t...'
2025-05-15 15:57:56,287 - INFO - 🔄 Mixed script text detected: 'बहुत अची super...'
2025-05-15 16:00:46,487 - INFO - 🔄 Mixed script text detected: 'All services is good 💯। Well done ✅👍 uco bank …...'
2025-05-15 16:08:53,062 - INFO - 🔄 Mixed script text detected: 'Service is 

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Matching topics:   0%|                                                               | 1/19641 [00:00<48:38,  6.73it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Matching topics: 100%|██████████████████████████████████████████████████████████▉| 19639/19641 [22:57<00:00, 16.85it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Matching topics: 100%|███████████████████████████████████████████████████████████| 19641/19641 [22:57<00:00, 14.26it/s]
2025-05-15 18:29:23,059 - INFO - 🔄 Combining results...
2025-05-15 18:29:23,786 - INFO - ✨ Final output saved to: C:\Users\rzzzc\BFARPy\Python\4th Sem\UCO_google_review_scrapping\Sentiment_analysis\reviews_sentiment_topic.csv (UTF-8 with BOM)
2025-05-15 18:29:23,787 - INFO - 📊 Processing Summary:
2025-05-15 18:29:23,789 - INFO -    - Total reviews processed: 19641
2025-05-15 18:29:23,802 - INFO -    - Topic distribution: {'Other / Unclassified': 18833, 'account opening issues': 412, 'ATM withdrawal issues': 247, 'mobile app issues': 84, 'fraud / unauthorized transaction': 30, 'UPI issues': 11, 'debit card issues': 8, 'KYC / CKYC issues': 6, 'internet banking issues': 6, 'IMPS / NEFT / RTGS issues': 3, 'credit card issues': 1}
2025-05-15 18:29:23,807 - INFO -    - Sentiment distribution: {'positive': 13346, 'negative': 4639, 'neutral': 1656}
